# Capstone Project - The Neighborhoods of New York
### Applied Data Science Capstone by Carlos Alberto Jimenez Ferrer

## Table of contents
* [Introduction](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Discussion](#discussion)
* [Conclusion](#conclusion)

## Introduction <a name="introduction"></a>

#### 1.1.	Background
New York City, officially the City of New York. It is the largest and most influential American metropolis. New York City is in reality a collection of many neighborhoods scattered among the city’s five boroughs which are Bronx, Brooklyn, Manhattan, Queens, and Staten Island each exhibiting its own characteristics and ways of life. They say that moving from one city neighborhood to the next may be like passing from one country to another. Therefore, it is advantageous to know how each neighborhood is similar one to another in each borough.
#### 1.2.	Problem
The data that contribute to the classification of each neighborhood include the top most common venues found in each of the neighborhood. This project aims to cluster by similarity each cluster in all boroughs and finally give a general analysis of the complete New York City, comparing all the neighborhood in the city.
#### 1.3.	Interest
It works for everyone trying to move (for many reasons, be it moving because of job or trying to move closer to a specific school), this information can be useful to know more about those similar neighborhoods. Other who may be interested can be real estate agent looking to improve their options when offering a more similar property in terms of venues nearby.


## Data <a name="data"></a>

#### 2.1.	Data sources
The data was acquired thanks to the city of New York open data that can be found in this link clicking https://opendata.cityofnewyork.us/. The dataset that we used was the one of Neighborhood Names GIS that the link can be found https://data.cityofnewyork.us/City-Government/Neighborhood-Names-GIS/99bc-9p23. The data contains the geolocation, object id, name, stacked, borough, Annoline1, Annoline2, Annoline3, AnnoAngle of each neighborhood. We will use this data to classify each of the neighborhoods. We will be using the foursquare API to get the list of venues nearby to the target neighborhoods and with this information we will do our analysis.



#### 2.2.	Data cleaning
The data was downloaded but to work with the dataset I had to make a few changes in the dataset. First of all I had to eliminate some columns that wouldn’t contribute at all with the analysis like stacked, Annoline1, Annoline2, Annoline3, and AnnoAngle. After doing the dropping of each of the columns there was another problem to work with, the_geom (the geolocation column) in each row had a format of POINT (Longitude, Latitude) so I had to eliminate first of all the point and the parentheses and after that separate the longitude and the latitude in different columns for each row. After doing all this the data frame was ready so I could work with it.
 After all the cleaning I divided the data frames in six different frames, one of each borough and the final one is of the whole list of neighborhoods in New York, each with their latitude and longitude.
 I had some problems in the Staten Island analysis with the foursquare API with a neighborhood that wasn’t returning close by venues so in the analysis I had to drop it. And in the New York analysis with a neighborhood of name ‘Chelsea’ that was getting duplicated.


First let´s import all the libraries that we will need.

In [1]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json # library to handle JSON files
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
import matplotlib.cm as cm
import matplotlib.colors as colors
# import k-means from clustering stage
from sklearn.cluster import KMeans
!conda install -c conda-forge folium=0.5.0 --yes
import folium # map rendering library
print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    ca-certificates-2020.4.5.1 |       hecc5488_0         146 KB  conda-forge
    branca-0.4.0               |             py_0          26 KB  conda-forge
    certifi-2020.4.5.1         |   py36h9f0ad1d_0         151 KB  conda-forge
    openssl-1.1.1f             |       h516909a_0         2.1 MB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    ------------------------------------------------------------
                       

In [2]:
csv_path = 'https://data.cityofnewyork.us/api/views/xyye-rtrs/rows.csv?accessType=DOWNLOAD&bom=true&format=true'
nydf = pd.read_csv(csv_path)

In [3]:
nydf

the_geom  OBJECTID  \
0      POINT (-73.8472005205491 40.89470517661004)         1   
1     POINT (-73.82993910812405 40.87429419303015)         2   
2     POINT (-73.82780644716419 40.88755567735082)         3   
3    POINT (-73.90564259591689 40.895437426903875)         4   
4     POINT (-73.91258546108577 40.89083449389134)         5   
5     POINT (-73.90281798724611 40.88168737120525)         6   
6     POINT (-73.91065965862988 40.87655077879968)         7   
7    POINT (-73.86731496814183 40.898272612138086)         8   
8    POINT (-73.87939073956817 40.877224155994504)         9   
9     POINT (-73.85744642974214 40.88103887819214)        10   
10    POINT (-73.83579759808124 40.86685810725274)        11   
11    POINT (-73.85475564018006 40.85741349808869)        12   
12     POINT (-73.7864884526742 40.84724670491817)        13   
13    POINT (-73.88551218419137 40.87018516497537)        14   
14    POINT (-73.91041596191317 40.85572707719668)        15   
15    POINT (-73.91967159119572 40.84789792606274)        16   
16     POINT (-73.8964265598163 40.86099679638657)        17   
17    POINT (-73.88735617532345 40.84269615786057)        18   
18    POINT (-73.87774474910552 40.83947505672657)        19   
19     POINT (-73.92610209358138 40.8366230107061)        20   
20    POINT (-73.90942160757443 40.81975437059498)        21   
21    POINT (-73.91609987487583 40.80623874935181)        22   
22    POINT (-73.91322139386142 40.80166362775625)        23   
23   POINT (-73.89578820094466 40.815099045458254)        24   
24   POINT (-73.88331505955298 40.809729879387135)        25   
25    POINT (-73.90150648943066 40.82359198585537)        26   
26    POINT (-73.86574609554933 40.82101219791406)        27   
27   POINT (-73.85414416189273 40.806551120035934)        28   
28    POINT (-73.8163500215845 40.815109258040096)        29   
29    POINT (-73.82409926753857 40.84424593694742)        30   
30     POINT (-73.8560031053579 40.83793782226733)        31   
31    POINT (-73.8421940760445 40.840619496432744)        32   
32    POINT (-73.86629918075617 40.84360847124722)        33   
33    POINT (-73.85040178030428 40.84754906353638)        34   
34    POINT (-73.88845196134812 40.85727710073898)        35   
35       POINT (-73.917190482104 40.8813949772709)        36   
36     POINT (-73.90453054908934 40.9085428295067)        37   
37    POINT (-73.83207378240478 40.85064140940339)        38   
38    POINT (-73.82620275994081 40.82657951686926)        39   
39    POINT (-73.81388514428627 40.82198611816354)        40   
40    POINT (-73.84802729582742 40.81901437698835)        41   
41    POINT (-73.86332361652784 40.87137078192375)        42   
42    POINT (-73.8416119483123 40.862965624780024)        43   
43   POINT (-73.91558941773451 40.834283807338544)        44   
44    POINT (-73.85053524451942 40.82977429787165)        45   
45    POINT (-73.84808271877175 40.88456130303736)        46   
46    POINT (-74.03062069353821 40.62580106501069)        47   
47    POINT (-73.99517998380736 40.61100890202048)        48   
48    POINT (-74.01031618527792 40.64510294925433)        49   
49     POINT (-73.954240931274 40.730200984864744)        50   
50    POINT (-73.97347087708452 40.59526001306597)        51   
51   POINT (-73.96509448785343 40.576825065666085)        52   
52    POINT (-73.94318640482987 40.58689012678388)        53   
53    POINT (-73.95743840559946 40.61443251335102)        54   
54    POINT (-73.95840106533912 40.63632589026681)        55   
55     POINT (-73.9432911907359 40.67082917695298)        56   
56    POINT (-73.93610256185843 40.64171776668965)        57   
57    POINT (-73.98042110559481 40.64238195800357)        58   
58    POINT (-73.98007340430179 40.65694583575108)        59   
59    POINT (-73.96485924262697 40.67682226225477)        60   
60    POINT (-73.91023536176615 40.66394994339758)        61   
61    POINT (-73.95811529220936 40.70714439344255)        62   
62    POIN

In [4]:
nydf.drop(['OBJECTID','Stacked','AnnoLine1', 'AnnoLine2', 'AnnoLine3', 'AnnoAngle'], axis=1).head()

the_geom         Name Borough
0    POINT (-73.8472005205491 40.89470517661004)    Wakefield   Bronx
1   POINT (-73.82993910812405 40.87429419303015)   Co-op City   Bronx
2   POINT (-73.82780644716419 40.88755567735082)  Eastchester   Bronx
3  POINT (-73.90564259591689 40.895437426903875)    Fieldston   Bronx
4   POINT (-73.91258546108577 40.89083449389134)    Riverdale   Bronx

In [5]:
nydf = nydf[['Borough','Name','the_geom']]
nydf.head()

Borough         Name                                       the_geom
0   Bronx    Wakefield    POINT (-73.8472005205491 40.89470517661004)
1   Bronx   Co-op City   POINT (-73.82993910812405 40.87429419303015)
2   Bronx  Eastchester   POINT (-73.82780644716419 40.88755567735082)
3   Bronx    Fieldston  POINT (-73.90564259591689 40.895437426903875)
4   Bronx    Riverdale   POINT (-73.91258546108577 40.89083449389134)

In [6]:
nydf.dtypes

Borough     object
Name        object
the_geom    object
dtype: object

In [7]:
test = nydf
test.head()

Borough         Name                                       the_geom
0   Bronx    Wakefield    POINT (-73.8472005205491 40.89470517661004)
1   Bronx   Co-op City   POINT (-73.82993910812405 40.87429419303015)
2   Bronx  Eastchester   POINT (-73.82780644716419 40.88755567735082)
3   Bronx    Fieldston  POINT (-73.90564259591689 40.895437426903875)
4   Bronx    Riverdale   POINT (-73.91258546108577 40.89083449389134)

In [8]:
# start stop and step variables 
start, stop, step = 7, -1, 1

# converting to string data type 
test["the_geom"]= test["the_geom"].astype(str) 

# slicing till 2nd last element 
test["geolocation"]= test["the_geom"].str.slice(start, stop, step) 

# display 
test.head()

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


Borough         Name                                       the_geom  \
0   Bronx    Wakefield    POINT (-73.8472005205491 40.89470517661004)   
1   Bronx   Co-op City   POINT (-73.82993910812405 40.87429419303015)   
2   Bronx  Eastchester   POINT (-73.82780644716419 40.88755567735082)   
3   Bronx    Fieldston  POINT (-73.90564259591689 40.895437426903875)   
4   Bronx    Riverdale   POINT (-73.91258546108577 40.89083449389134)   

                             geolocation  
0    -73.8472005205491 40.89470517661004  
1   -73.82993910812405 40.87429419303015  
2   -73.82780644716419 40.88755567735082  
3  -73.90564259591689 40.895437426903875  
4   -73.91258546108577 40.89083449389134

In [9]:
test.drop(['the_geom'], axis=1).head()

Borough         Name                            geolocation
0   Bronx    Wakefield    -73.8472005205491 40.89470517661004
1   Bronx   Co-op City   -73.82993910812405 40.87429419303015
2   Bronx  Eastchester   -73.82780644716419 40.88755567735082
3   Bronx    Fieldston  -73.90564259591689 40.895437426903875
4   Bronx    Riverdale   -73.91258546108577 40.89083449389134

In [10]:
# new data frame with split value columns 
new = test["geolocation"].str.split(" ", n = 1, expand = True) 
  
# making separate first name column from new data frame 
test["Longitude"]= new[0] 
  
# making separate last name column from new data frame 
test["Latitude"]= new[1] 
  
# Dropping old Name columns 
test.drop(columns =["geolocation"], inplace = True) 
  
# df display 
test.head()

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors

Borough         Name                                       the_geom  \
0   Bronx    Wakefield    POINT (-73.8472005205491 40.89470517661004)   
1   Bronx   Co-op City   POINT (-73.82993910812405 40.87429419303015)   
2   Bronx  Eastchester   POINT (-73.82780644716419 40.88755567735082)   
3   Bronx    Fieldston  POINT (-73.90564259591689 40.895437426903875)   
4   Bronx    Riverdale   POINT (-73.91258546108577 40.89083449389134)   

            Longitude            Latitude  
0   -73.8472005205491   40.89470517661004  
1  -73.82993910812405   40.87429419303015  
2  -73.82780644716419   40.88755567735082  
3  -73.90564259591689  40.895437426903875  
4  -73.91258546108577   40.89083449389134

In [11]:
test.drop(columns =["the_geom"], inplace = True) 

In [12]:
test.head()

Borough         Name           Longitude            Latitude
0   Bronx    Wakefield   -73.8472005205491   40.89470517661004
1   Bronx   Co-op City  -73.82993910812405   40.87429419303015
2   Bronx  Eastchester  -73.82780644716419   40.88755567735082
3   Bronx    Fieldston  -73.90564259591689  40.895437426903875
4   Bronx    Riverdale  -73.91258546108577   40.89083449389134

In [13]:
nydf = test

In [14]:
nydf.head()

Borough         Name           Longitude            Latitude
0   Bronx    Wakefield   -73.8472005205491   40.89470517661004
1   Bronx   Co-op City  -73.82993910812405   40.87429419303015
2   Bronx  Eastchester  -73.82780644716419   40.88755567735082
3   Bronx    Fieldston  -73.90564259591689  40.895437426903875
4   Bronx    Riverdale  -73.91258546108577   40.89083449389134

In [15]:
convert_dict = {'Latitude': float, 
                'Longitude': float
               } 
  
nydf = nydf.astype(convert_dict) 
print(nydf.dtypes) 

Borough       object
Name          object
Longitude    float64
Latitude     float64
dtype: object


In [16]:
nydf = nydf[['Borough','Name','Latitude','Longitude']]
nydf.head()

Borough         Name   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [17]:
nydf.sort_values(by=['Borough'], inplace = True)

Now lets create a dataframe for each borough

In [18]:
nydf.reset_index(inplace = True)

In [19]:
nydf.drop(columns =["index"], inplace = True) 

In [20]:
nydf.head()

Borough          Name   Latitude  Longitude
0   Bronx     Wakefield  40.894705 -73.847201
1   Bronx  Clason Point  40.806551 -73.854144
2   Bronx   Throgs Neck  40.815109 -73.816350
3   Bronx  Country Club  40.844246 -73.824099
4   Bronx   Parkchester  40.837938 -73.856003

Lets check the size

In [21]:
nydf.shape

(299, 4)

In [22]:
bronxdf, brooklyndf, manhdf, queendf, statisdf = nydf[:49], nydf[49:120], nydf[120:159], nydf[159:237], nydf[237:]

In [23]:
bronxdf.head()

Borough          Name   Latitude  Longitude
0   Bronx     Wakefield  40.894705 -73.847201
1   Bronx  Clason Point  40.806551 -73.854144
2   Bronx   Throgs Neck  40.815109 -73.816350
3   Bronx  Country Club  40.844246 -73.824099
4   Bronx   Parkchester  40.837938 -73.856003

In [24]:
brooklyndf.head()

Borough                 Name   Latitude  Longitude
49  Brooklyn    East Williamsburg  40.708492 -73.938858
50  Brooklyn         Spring Creek  40.657139 -73.869988
51  Brooklyn           Georgetown  40.623845 -73.916075
52  Brooklyn  Prospect Park South  40.647009 -73.962613
53  Brooklyn              Midwood  40.625596 -73.957595

In [25]:
manhdf.head()

Borough          Name   Latitude  Longitude
120  Manhattan      Flatiron  40.739673 -73.990947
121  Manhattan  Civic Center  40.715229 -74.005415
122  Manhattan    Tudor City  40.746917 -73.971219
123  Manhattan    Turtle Bay  40.752042 -73.967708
124  Manhattan  Sutton Place  40.760280 -73.963556

In [26]:
queendf.head()

Borough             Name   Latitude  Longitude
159  Queens  Queensboro Hill  40.744572 -73.825809
160  Queens       Somerville  40.597711 -73.796648
161  Queens    Rockaway Park  40.580343 -73.841534
162  Queens     Belle Harbor  40.576156 -73.854018
163  Queens      Lefrak City  40.736075 -73.862525

In [27]:
statisdf.head()

Borough              Name   Latitude  Longitude
237  Staten Island       Grymes Hill  40.624185 -74.087248
238  Staten Island         Todt Hill  40.597069 -74.111329
239  Staten Island       South Beach  40.580247 -74.079553
240  Staten Island     Port Richmond  40.633669 -74.129434
241  Staten Island  Mariner's Harbor  40.632546 -74.150085

Now lets drop the borough and reset the index in all of them

In [28]:
bronxdf.drop(columns =["Borough"], inplace = True) 
brooklyndf.drop(columns =["Borough"], inplace = True) 
manhdf.drop(columns =["Borough"], inplace = True) 
queendf.drop(columns =["Borough"], inplace = True) 
statisdf.drop(columns =["Borough"], inplace = True) 

In [29]:
bronxdf.reset_index(inplace = True)
brooklyndf.reset_index(inplace = True)
manhdf.reset_index(inplace = True)
queendf.reset_index(inplace = True)
statisdf.reset_index(inplace = True)

Lets drop again the index column of all dataframes

In [30]:
bronxdf.drop(columns =["index"], inplace = True) 
brooklyndf.drop(columns =["index"], inplace = True) 
manhdf.drop(columns =["index"], inplace = True) 
queendf.drop(columns =["index"], inplace = True) 
statisdf.drop(columns =["index"], inplace = True) 

Lets check the size of our new dataframes

In [31]:
bronxdf.shape

(49, 3)

In [32]:
brooklyndf.shape

(71, 3)

In [33]:
manhdf.shape

(39, 3)

In [34]:
queendf.shape

(78, 3)

In [35]:
statisdf.shape

(62, 3)

## Methodology <a name="methodology"></a>

We will use the k-means method to cluster each of the neighborhoods, first I used the foursquare API to get the venues, now that we have a list of venues, I applied an onehot coding procedure in which we classified what type of venues it was. With the onehot coding now what we have to do its group each in the list with the corresponding neighborhood and with this we can calculate the frequency that each type of venue appears. Now what we have the frequency we can actually pick the top ten most common venue in each neighborhood.
 Now that we have a data frame with the top type of venues in each neighborhood we can proceed to start the clustering process, for this type of process the amount of cluster will decide the amount of difference that you will find in the clustered map. So for each borough I decide to put 5 cluster and for the final one of New York I decided to work with 8 cluster, the reasons being the amount of neighborhood that we can find in that map.
 Now we can plot in a map the k-means clustering that we did and finally we can show which neighborhoods and their top picks are in each cluster so we can do an analysis of each cluster and look at their properties and comment which cluster is the most common to find in each borough and in New York.

## Analysis <a name="analysis"></a>

### Use geopy library to get the latitude and longitude values of New York City.

In [36]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


### Create a map of New York with neighborhoods superimposed on top.

In [37]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, name in zip(nydf['Latitude'], nydf['Longitude'], nydf['Borough'], nydf['Name']):
    label = '{}, {}'.format(name, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

# Now lets visualize each of the neighborhoods in each borough

## Bronx

Let's get the geographical coordinates of Bronx.

In [38]:
address = 'Bronx, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitudebx = location.latitude
longitudebx = location.longitude
print('The geograpical coordinate of Bronx are {}, {}.'.format(latitudebx, longitudebx))

The geograpical coordinate of Bronx are 40.8466508, -73.8785937.


Lets visualize it

In [39]:
# create map of Bronx using latitude and longitude values
map_bronx = folium.Map(location=[latitudebx, longitudebx], zoom_start=11)

# add markers to map
for lat, lng, label in zip(bronxdf['Latitude'], bronxdf['Longitude'], bronxdf['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_bronx)  
    
map_bronx

## Brooklyn

Let's get the geographical coordinates of Brooklyn.

In [40]:
address = 'Brooklyn, NY'

geolocator = Nominatim(user_agent="ny_explorer")
locationb = geolocator.geocode(address)
latitudeb = 40.6782 #location.latitude there is a problem with this adress so we put the input manually
longitudeb = -73.9442 #location.longitude there is a problem with this adress so we put the input manually
print('The geograpical coordinate of Brooklyn are {}, {}.'.format(latitudeb, longitudeb))

The geograpical coordinate of Brooklyn are 40.6782, -73.9442.


Lets visualize it

In [41]:
# create map of Brooklyn using latitude and longitude values
map_brooklyn = folium.Map(location=[latitudeb, longitudeb], zoom_start=11)

# add markers to map
for lat, lng, label in zip(brooklyndf['Latitude'], brooklyndf['Longitude'], brooklyndf['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_brooklyn)  
    
map_brooklyn

## Manhattan

Let's get the geographical coordinates of Manhattan.

In [42]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitudem = location.latitude
longitudem = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitudem, longitudem))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


Lets visualize it

In [43]:
# create map of Manhattan using latitude and longitude values
map_manhattan = folium.Map(location=[latitudem, longitudem], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhdf['Latitude'], manhdf['Longitude'], manhdf['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)
    
map_manhattan

## Queens

Let's get the geographical coordinates of Queens.

In [44]:
address = 'Queens, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitudeq = location.latitude
longitudeq = location.longitude
print('The geograpical coordinate of Queens are {}, {}.'.format(latitudeq, longitudeq))

The geograpical coordinate of Queens are 40.7498243, -73.7976337.


Lets visualize it

In [45]:
# create map of Queens using latitude and longitude values
map_queens = folium.Map(location=[latitudeq, longitudeq], zoom_start=11)

# add markers to map
for lat, lng, label in zip(queendf['Latitude'], queendf['Longitude'], queendf['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_queens)
    
map_queens

## Staten Island

Let's get the geographical coordinates of Staten Island.

In [46]:
address = 'Staten Island, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitudest = location.latitude
longitudest = location.longitude
print('The geograpical coordinate of Queens are {}, {}.'.format(latitudest, longitudest))

The geograpical coordinate of Queens are 40.5834557, -74.1496048.


Lets visualize it

In [47]:
# create map of Staten Island using latitude and longitude values
map_staten = folium.Map(location=[latitudest, longitudest], zoom_start=11)

# add markers to map
for lat, lng, label in zip(statisdf['Latitude'], statisdf['Longitude'], statisdf['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_staten)
    
map_staten

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

## Define Foursquare Credentials and Version

In [48]:
CLIENT_ID = 'Y2NOK5O4RUUXXJ1YJPTN0UMPTB1RP31PMDVWQL02TIYAMCLP' # your Foursquare ID
CLIENT_SECRET = 'QCKBTGTI0YWNBMBGKBJ4YW45X4XKW5EYS0AAKJC5JIKBFHAI' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version #20180605
LIMIT = 100

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: Y2NOK5O4RUUXXJ1YJPTN0UMPTB1RP31PMDVWQL02TIYAMCLP
CLIENT_SECRET:QCKBTGTI0YWNBMBGKBJ4YW45X4XKW5EYS0AAKJC5JIKBFHAI


## Explore Neighborhoods in Bronx

In [49]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

LEts write the code to run the above function on each neighborhood and create a new dataframe called manhattan_venues

In [50]:
bronx_venues = getNearbyVenues(names=bronxdf['Name'],
                                   latitudes=bronxdf['Latitude'],
                                   longitudes=bronxdf['Longitude'],
                              )

Wakefield
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Soundview
Pelham Bay
Edgewater Park
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Mount Hope
Mount Eden
Concourse Village
Claremont Village
Schuylerville
Morrisania
Castle Hill
Longwood
Co-op City
Hunts Point
Fieldston
Riverdale
Kingsbridge
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
Eastchester
Bedford Park
Melrose
High  Bridge
Mott Haven
West Farms
City Island
Fordham
Morris Heights
University Heights
East Tremont
Port Morris


### Let's check the size of the resulting dataframe

In [51]:
print(bronx_venues.shape)
bronx_venues.head()

(1140, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3         Walgreens       40.896528       -73.844700        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [52]:
bronx_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                               
Baychester                             23                      23     23   
Bedford Park                           37                      37     37   
Belmont                               100                     100    100   
Castle Hill                             9                       9      9   
City Island                            27                      27     27   
Claremont Village                      19                      19     19   
Clason Point                           10                      10     10   
Co-op City                             16                      16     16   
Concourse                              24                      24     24   
Concourse Village                      35                      35     35   
Country Club                            4                       4      4   
East Tremont                           19                      19     19   
Eastchester                            19                      19     19   
Edenwald                                5                       5      5   
Edgewater Park                         19                      19     19   
Fieldston                               3                       3      3   
Fordham                                87                      87     87   
High  Bridge                           24                      24     24   
Hunts Point                            12                      12     12   
Kingsbridge                            68                      68     68   
Longwood                                8                       8      8   
Melrose                                25                      25     25   
Morris Heights                          8                       8      8   
Morris Park                            23                      23     23   
Morrisania                             23                      23     23   
Mott Haven                             21                      21     21   
Mount Eden                             32                      32     32   
Mount Hope                             11                      11     11   
North Riverdale                        22                      22     22   
Norwood                                29                      29     29   
Olinville                              12                      12     12   
Parkchester                            36                      36     36   
Pelham Bay                             42                      42     42   
Pelham Gardens                         18                      18     18   
Pelham Parkway                         24                      24     24   
Port Morris                            11                      11     11   
Riverdale                              11                      11     11   
Schuylerville                          19                      19     19   
Soundview                              16                      16     16   
Spuyten Duyvil                          8                       8      8   
Throgs Neck                            13                      13     13   
Unionport                              22                      22     22   
University Heights                     22                      22     22   
Van Nest                               27                      27     27   
Wakefield                              10                      10     10   
West Farms                             23                      23     23   
Westchester Square                     35                      35     35   
Williamsbridge                          4                       4      4   
Woodlawn                               25                      25     25   

                    Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                         
Bay

Let's find out how many unique categories can be curated from all the returned venues

In [53]:
print('There are {} uniques categories.'.format(len(bronx_venues['Venue Category'].unique())))

There are 165 uniques categories.


## Analyze Each Neighborhood of Bronx

In [54]:
bronx_onehot = pd.get_dummies(bronx_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
bronx_onehot['Neighborhood'] = bronx_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [bronx_onehot.columns[-1]] + list(bronx_onehot.columns[:-1])
bronx_onehot = bronx_onehot[fixed_columns]

bronx_onehot.head()

Neighborhood  Accessories Store  African Restaurant  American Restaurant  \
0    Wakefield                  0                   0                    0   
1    Wakefield                  0                   0                    0   
2    Wakefield                  0                   0                    0   
3    Wakefield                  0                   0                    0   
4    Wakefield                  0                   0                    0   

   Antique Shop  Arcade  Arepa Restaurant  Art Gallery  Art Museum  \
0             0       0                 0            0           0   
1             0       0                 0            0           0   
2             0       0                 0            0           0   
3             0       0                 0            0           0   
4             0       0                 0            0           0   

   Asian Restaurant  Athletics & Sports  BBQ Joint  Bagel Shop  Bakery  Bank  \
0                 0                   0          0           0       0     0   
1                 0                   0          0           0       0     0   
2                 0                   0          0           0       0     0   
3                 0                   0          0           0       0     0   
4                 0                   0          0           0       0     0   

   Bar  Baseball Field  Basketball Court  Beer Bar  Boat or Ferry  Bookstore  \
0    0               0                 0         0              0          0   
1    0               0                 0         0              0          0   
2    0               0                 0         0              0          0   
3    0               0                 0         0              0          0   
4    0               0                 0         0              0          0   

   Bowling Alley  Breakfast Spot  Brewery  Buffet  Building  Burger Joint  \
0              0               0        0       0         0             0   
1              0               0        0       0         0             0   
2              0               0        0       0         0             0   
3              0               0        0       0         0             0   
4              0               0        0       0         0             0   

   Bus Line  Bus Station  Bus Stop  Café  Candy Store  Caribbean Restaurant  \
0         0            0         0     0            0                     0   
1         0            0         0     0            0                     0   
2         0            0         0     0            0                     0   
3         0            0         0     0            0                     0   
4         0            0         0     0            0                     0   

   Check Cashing Service  Cheese Shop  Chinese Restaurant  Clothing Store  \
0                      0            0                   0               0   
1                      0            0                   0               0   
2                      0            0                   0               0   
3                      0            0                   0               0   
4                      0            0                   0               0   

   Coffee Shop  Comfort Food Restaurant  Convenience Store  Cosmetics Shop  \
0            0                        0                  0               0   
1            0                        0                  0               0   
2            0                        0                  0               0   
3            0                        0                  0               0   
4            0                        0                  0               0   

   Dance Studio  Deli / Bodega  Department Store  Dessert Shop  Diner  \
0             0              0                 0             1      0   
1             0              0                 0             0      0   
2             0              0                 0             

And let's examine the new dataframe size.

In [55]:
bronx_onehot.shape

(1140, 166)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [56]:
bronx_grouped = bronx_onehot.groupby('Neighborhood').mean().reset_index()
bronx_grouped

Neighborhood  Accessories Store  African Restaurant  \
0           Baychester           0.000000            0.000000   
1         Bedford Park           0.000000            0.000000   
2              Belmont           0.000000            0.000000   
3          Castle Hill           0.000000            0.000000   
4          City Island           0.000000            0.000000   
5    Claremont Village           0.000000            0.000000   
6         Clason Point           0.000000            0.000000   
7           Co-op City           0.062500            0.000000   
8            Concourse           0.000000            0.000000   
9    Concourse Village           0.000000            0.000000   
10        Country Club           0.000000            0.000000   
11        East Tremont           0.000000            0.000000   
12         Eastchester           0.000000            0.000000   
13            Edenwald           0.000000            0.000000   
14      Edgewater Park           0.000000            0.000000   
15           Fieldston           0.000000            0.000000   
16             Fordham           0.011494            0.011494   
17        High  Bridge           0.000000            0.000000   
18         Hunts Point           0.000000            0.000000   
19         Kingsbridge           0.000000            0.000000   
20            Longwood           0.000000            0.000000   
21             Melrose           0.000000            0.000000   
22      Morris Heights           0.000000            0.000000   
23         Morris Park           0.000000            0.000000   
24          Morrisania           0.000000            0.000000   
25          Mott Haven           0.000000            0.000000   
26          Mount Eden           0.000000            0.000000   
27          Mount Hope           0.000000            0.000000   
28     North Riverdale           0.000000            0.000000   
29             Norwood           0.000000            0.000000   
30           Olinville           0.000000            0.000000   
31         Parkchester           0.000000            0.000000   
32          Pelham Bay           0.000000            0.000000   
33      Pelham Gardens           0.000000            0.000000   
34      Pelham Parkway           0.000000            0.000000   
35         Port Morris           0.000000            0.000000   
36           Riverdale           0.000000            0.000000   
37       Schuylerville           0.000000            0.000000   
38           Soundview           0.000000            0.000000   
39      Spuyten Duyvil           0.000000            0.000000   
40         Throgs Neck           0.000000            0.000000   
41           Unionport           0.000000            0.000000   
42  University Heights           0.000000            0.045455   
43            Van Nest           0.000000            0.000000   
44           Wakefield           0.000000            0.000000   
45          West Farms           0.000000            0.000000   
46  Westchester Square           0.000000            0.000000   
47      Williamsbridge           0.000000            0.000000   
48            Woodlawn           0.000000            0.000000   

    American Restaurant  Antique Shop    Arcade  Arepa Restaurant  \
0              0.000000      0.000000  0.043478          0.000000   
1              0.000000      0.000000  0.000000          0.000000   
2              0.010000      0.000000  0.000000          0.000000   
3              0.000000      0.000000  0.000000          0.000000   
4              0.037037      0.000000  0.000000          0.000000   
5              0.000000      0.000000  0.000000          0.000000   
6              0.100000      0.000000  0.000000          0.000000   
7              0.000000      0.000000  0.000000          0.000000   
8              0.000000      0.000000  0.000000          0.000000   
9              0.000000      0.000000  0.000000          0.000000   


Lets check the size again

In [57]:
bronx_grouped.shape

(49, 166)

#### Let's print each neighborhood along with the top 5 most common venues

In [58]:
num_top_venues = 5

for hood in bronx_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = bronx_grouped[bronx_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Baychester----
                  venue  freq
0            Donut Shop  0.09
1         Moving Target  0.04
2  Gym / Fitness Center  0.04
3            Playground  0.04
4     Electronics Store  0.04


----Bedford Park----
                venue  freq
0               Diner  0.11
1         Bus Station  0.08
2       Deli / Bodega  0.08
3  Chinese Restaurant  0.08
4         Pizza Place  0.08


----Belmont----
                venue  freq
0  Italian Restaurant  0.18
1         Pizza Place  0.09
2       Deli / Bodega  0.08
3              Bakery  0.05
4          Donut Shop  0.03


----Castle Hill----
           venue  freq
0    Pizza Place  0.22
1         Market  0.11
2  Deli / Bodega  0.11
3          Diner  0.11
4       Pharmacy  0.11


----City Island----
                    venue  freq
0         Harbor / Marina  0.11
1                    Park  0.07
2      Seafood Restaurant  0.07
3  Thrift / Vintage Store  0.07
4          Ice Cream Shop  0.04


----Claremont Village----
           venue  freq

                       venue  freq
0                Bus Station  0.13
1                   Bus Stop  0.09
2             Ice Cream Shop  0.04
3  Latin American Restaurant  0.04
4               Intersection  0.04


----Westchester Square----
                  venue  freq
0  Fast Food Restaurant  0.09
1           Pizza Place  0.06
2            Donut Shop  0.06
3              Pharmacy  0.06
4        Sandwich Place  0.06


----Williamsbridge----
                  venue  freq
0            Soup Place  0.25
1             Nightclub  0.25
2                   Bar  0.25
3  Caribbean Restaurant  0.25
4     Accessories Store  0.00


----Woodlawn----
               venue  freq
0                Pub  0.12
1        Pizza Place  0.12
2  Food & Drink Shop  0.08
3         Playground  0.08
4      Deli / Bodega  0.08




#### Let's put that into a pandas dataframe

First, let's write a function to sort the venues in descending order.

In [59]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [60]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedBronx = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedBronx['Neighborhood'] = bronx_grouped['Neighborhood']

for ind in np.arange(bronx_grouped.shape[0]):
    neighborhoods_venues_sortedBronx.iloc[ind, 1:] = return_most_common_venues(bronx_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedBronx.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0    Baychester            Donut Shop     Convenience Store   
1  Bedford Park                 Diner           Bus Station   
2       Belmont    Italian Restaurant           Pizza Place   
3   Castle Hill           Pizza Place                  Bank   
4   City Island       Harbor / Marina                  Park   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0     Fried Chicken Joint        Mattress Store           Bus Station   
1           Deli / Bodega           Pizza Place    Chinese Restaurant   
2           Deli / Bodega                Bakery          Dessert Shop   
3                   Diner                  Park           Bus Station   
4  Thrift / Vintage Store    Seafood Restaurant        Ice Cream Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Sandwich Place    Mexican Restaurant         Boat or Ferry   
1        Sandwich Place    Mexican Restaurant                Bakery   
2    Mexican Restaurant            Donut Shop         Grocery Store   
3         Deli / Bodega                Market              Pharmacy   
4                   Bar           Music Venue              Pharmacy   

  9th Most Common Venue 10th Most Common Venue  
0     Electronics Store     Spanish Restaurant  
1                   Pub             Donut Shop  
2                  Bank           Liquor Store  
3         Grocery Store        Doctor's Office  
4        History Museum            Pizza Place

# Clustering of the neighborhoods of Bronx

Run k-means to cluster the neighborhood into 5 clusters. We will do this process with each borough

In [61]:
# set number of clusters
kclusters = 5

bronx_grouped_clustering = bronx_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(bronx_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 2, 2, 0, 1, 0, 1, 1, 2], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [62]:
#neighborhoods_venues_sortedBronx.drop(['Cluster Labels'], axis = 1, inplace = True) #If you get the error that clusters are alredy inserted uncomment this.
#neighborhoods_venues_sortedBronx.head()

In [63]:
# add clustering labels
neighborhoods_venues_sortedBronx.insert(0, 'Cluster Labels', kmeans.labels_)

bronx_merged = bronxdf

# merge bronx_merged with bronxdf to add latitude/longitude for each neighborhood
bronx_merged = bronx_merged.join(neighborhoods_venues_sortedBronx.set_index('Neighborhood'), on='Name')

bronx_merged # check the last columns!

Name   Latitude  Longitude  Cluster Labels  \
0            Wakefield  40.894705 -73.847201               1   
1         Clason Point  40.806551 -73.854144               0   
2          Throgs Neck  40.815109 -73.816350               2   
3         Country Club  40.844246 -73.824099               3   
4          Parkchester  40.837938 -73.856003               2   
5   Westchester Square  40.840619 -73.842194               2   
6             Van Nest  40.843608 -73.866299               2   
7          Morris Park  40.847549 -73.850402               2   
8              Belmont  40.857277 -73.888452               2   
9       Spuyten Duyvil  40.881395 -73.917190               0   
10     North Riverdale  40.908543 -73.904531               2   
11           Soundview  40.821012 -73.865746               1   
12          Pelham Bay  40.850641 -73.832074               2   
13      Edgewater Park  40.821986 -73.813885               2   
14           Olinville  40.871371 -73.863324               2   
15      Pelham Gardens  40.862966 -73.841612               1   
16           Concourse  40.834284 -73.915589               1   
17           Unionport  40.829774 -73.850535               2   
18            Edenwald  40.884561 -73.848083               1   
19          Mount Hope  40.848842 -73.908299               2   
20          Mount Eden  40.843826 -73.916556               1   
21   Concourse Village  40.824780 -73.915847               2   
22   Claremont Village  40.831428 -73.901199               1   
23       Schuylerville  40.826580 -73.826203               2   
24          Morrisania  40.823592 -73.901506               1   
25         Castle Hill  40.819014 -73.848027               2   
26            Longwood  40.815099 -73.895788               1   
27          Co-op City  40.874294 -73.829939               1   
28         Hunts Point  40.809730 -73.883315               2   
29           Fieldston  40.895437 -73.905643               4   
30           Riverdale  40.890834 -73.912585               0   
31         Kingsbridge  40.881687 -73.902818               2   
32            Woodlawn  40.898273 -73.867315               2   
33             Norwood  40.877224 -73.879391               2   
34      Williamsbridge  40.881039 -73.857446               2   
35          Baychester  40.866858 -73.835798               2   
36      Pelham Parkway  40.857413 -73.854756               2   
37         Eastchester  40.887556 -73.827806               2   
38        Bedford Park  40.870185 -73.885512               2   
39             Melrose  40.819754 -73.909422               2   
40        High  Bridge  40.836623 -73.926102               2   
41          Mott Haven  40.806239 -73.916100               1   
42          West Farms  40.839475 -73.877745               0   
43         City Island  40.847247 -73.786488               0   
44             Fordham  40.860997 -73.896427               2   
45      Morris Heights  40.847898 -73.919672               1   
46  University Heights  40.855727 -73.910416               2   
47        East Tremont  40.842696 -73.887356               2   
48         Port Morris  40.801664 -73.913221               1   

   1st Most Common Venue      2nd Most Common Venue  \
0               Pharmacy                 Laundromat   
1                   Park  South American Restaurant   
2          Deli / Bodega                Coffee Shop   
3         Sandwich Place                        Spa   
4            Supermarket                Pizza Place   
5   Fast Food Restaurant                   Pharmacy   
6            Pizza Place              Deli / Bodega   
7            Pizza Place              Deli / Bodega   
8     Italian Restaurant                Pizza Place   
9                   Park                   Pharmacy   
10           Pizza Place                       Bank   
11    Chinese Restaurant              Grocery Store   
12    Italian Restaurant                       Bank   
13    Italian Restaurant                Pizza P

Let's visualize the resulting clusters

In [64]:
# create map
map_clustersBx = folium.Map(location=[latitudebx, longitudebx], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(bronx_merged['Latitude'], bronx_merged['Longitude'], bronx_merged['Name'], bronx_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersBx)
       
map_clustersBx


## Examine Clusters of Bronx

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

#### Cluster 1

In [200]:
bronx_merged.loc[bronx_merged['Cluster Labels'] == 0, bronx_merged.columns[[0] + list(range(4, bronx_merged.shape[1]))]]

Name 1st Most Common Venue      2nd Most Common Venue  \
1     Clason Point                  Park  South American Restaurant   
9   Spuyten Duyvil                  Park                   Pharmacy   
30       Riverdale                  Park                Bus Station   
42      West Farms           Bus Station                   Bus Stop   
43     City Island       Harbor / Marina                       Park   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
1      American Restaurant         Boat or Ferry                  Pool   
9                 Bus Line          Intersection       Thai Restaurant   
30            Home Service            Playground                 Plaza   
42                    Park        Scenic Lookout        Sandwich Place   
43  Thrift / Vintage Store    Seafood Restaurant        Ice Cream Shop   

   6th Most Common Venue 7th Most Common Venue        8th Most Common Venue  \
1          Grocery Store              Bus Stop                  Event Space   
9         Tennis Stadium                  Bank  Eastern European Restaurant   
30                   Gym  Medical Supply Store                   Food Truck   
42    Chinese Restaurant           Coffee Shop                   Playground   
43                   Bar           Music Venue                     Pharmacy   

   9th Most Common Venue 10th Most Common Venue  
1            Fish Market      Fish & Chips Shop  
9      Fish & Chips Shop            Film Studio  
30                  Bank          Women's Store  
42        Ice Cream Shop       Basketball Court  
43        History Museum            Pizza Place

#### Cluster 2

In [199]:
bronx_merged.loc[bronx_merged['Cluster Labels'] == 1, bronx_merged.columns[[0] + list(range(4, bronx_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
0           Wakefield              Pharmacy            Laundromat   
11          Soundview    Chinese Restaurant         Grocery Store   
15     Pelham Gardens    Spanish Restaurant           Bus Station   
16          Concourse         Grocery Store                Bakery   
18           Edenwald           Fish Market           Bus Station   
20         Mount Eden              Pharmacy    Spanish Restaurant   
22  Claremont Village         Grocery Store           Bus Station   
24         Morrisania        Discount Store         Grocery Store   
26           Longwood            Donut Shop                 Train   
27         Co-op City           Bus Station        Ice Cream Shop   
41         Mott Haven            Donut Shop    Spanish Restaurant   
45     Morris Heights              Pharmacy           Pizza Place   
48        Port Morris   Peruvian Restaurant            Restaurant   

   3rd Most Common Venue 4th Most Common Venue      5th Most Common Venue  \
0           Dessert Shop            Donut Shop       Caribbean Restaurant   
11           Bus Station              Bus Stop        Fried Chicken Joint   
15              Pharmacy            Donut Shop              Grocery Store   
16        Ice Cream Shop   Fried Chicken Joint               Dance Studio   
18           Supermarket           Gas Station              Grocery Store   
20  Fast Food Restaurant           Pizza Place              Deli / Bodega   
22                Bakery           Pizza Place             Discount Store   
24  Fast Food Restaurant            Donut Shop                Bus Station   
26  Fast Food Restaurant        Sandwich Place  Latin American Restaurant   
27            Restaurant            Bagel Shop             Baseball Field   
41           Pizza Place                   Gym              Grocery Store   
45         Grocery Store    Spanish Restaurant                       Bank   
48    Spanish Restaurant      Storage Facility                Music Venue   

        6th Most Common Venue      7th Most Common Venue  \
0              Sandwich Place              Deli / Bodega   
11               Liquor Store  Latin American Restaurant   
15              Boat or Ferry         Chinese Restaurant   
16                   Pharmacy                Pizza Place   
18              Women's Store                Event Space   
20  Latin American Restaurant                Bus Station   
22                       Park         Chinese Restaurant   
24             Ice Cream Shop              Bowling Alley   
26              Grocery Store              Metro Station   
27           Basketball Court         Chinese Restaurant   
41        Peruvian Restaurant                  Bookstore   
45  Latin American Restaurant                      Plaza   
48     Furniture / Home Store                    Brewery   

   8th Most Common Venue      9th Most Common Venue 10th Most Common Venue  
0            Gas Station             Ice Cream Shop          Grocery Store  
11        Breakfast Spot               Burger Joint               Pharmacy  
15                  Bank                 Playground         Sandwich Place  
16            Playground         Chinese Restaurant             Donut Shop  
18     Fish & Chips Shop                Film Studio   Fast Food Restaurant  
20    Seafood Restaurant          Mobile Phone Shop                 Buffet  
22  Caribbean Restaurant                       Food    Fried Chicken Joint  
24           Fish Market              Metro Station     Mexican Restaurant  
26                 Diner                 Distillery               Dive Bar  
27        Discount Store       Fast Food Restaurant          Grocery Store  
41     Mobile Phone Shop             Baseball Field       Storage Facility  
45                 Diner          Electronics Store          Deli / Bodega  
48            Donut Shop  Latin American Restaurant          Grocery Store

#### Cluster 3

In [198]:
bronx_merged.loc[bronx_merged['Cluster Labels'] == 2, bronx_merged.columns[[0] + list(range(4, bronx_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
2          Throgs Neck         Deli / Bodega           Coffee Shop   
4          Parkchester           Supermarket           Pizza Place   
5   Westchester Square  Fast Food Restaurant              Pharmacy   
6             Van Nest           Pizza Place         Deli / Bodega   
7          Morris Park           Pizza Place         Deli / Bodega   
8              Belmont    Italian Restaurant           Pizza Place   
10     North Riverdale           Pizza Place                  Bank   
12          Pelham Bay    Italian Restaurant                  Bank   
13      Edgewater Park    Italian Restaurant           Pizza Place   
14           Olinville           Supermarket          Liquor Store   
17           Unionport        Ice Cream Shop            Donut Shop   
19          Mount Hope           Pizza Place         Grocery Store   
21   Concourse Village  Fast Food Restaurant        Sandwich Place   
23       Schuylerville           Pizza Place   American Restaurant   
25         Castle Hill           Pizza Place                  Bank   
28         Hunts Point           Pizza Place         Grocery Store   
31         Kingsbridge           Pizza Place                   Bar   
32            Woodlawn                   Pub           Pizza Place   
33             Norwood           Pizza Place                  Bank   
34      Williamsbridge            Soup Place                   Bar   
35          Baychester            Donut Shop     Convenience Store   
36      Pelham Parkway           Pizza Place    Italian Restaurant   
37         Eastchester  Caribbean Restaurant         Deli / Bodega   
38        Bedford Park                 Diner           Bus Station   
39             Melrose           Pizza Place              Pharmacy   
40        High  Bridge              Pharmacy           Pizza Place   
44             Fordham  Fast Food Restaurant     Mobile Phone Shop   
46  University Heights           Pizza Place  Fast Food Restaurant   
47        East Tremont           Pizza Place        Breakfast Spot   

        3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
2                 Pizza Place      Italian Restaurant        Baseball Field   
4            Asian Restaurant     American Restaurant            Kids Store   
5                  Donut Shop          Sandwich Place           Pizza Place   
6   Middle Eastern Restaurant  Furniture / Home Store                Bakery   
7                Burger Joint                  Bakery           Supermarket   
8               Deli / Bodega                  Bakery          Dessert Shop   
10         Italian Restaurant          Ice Cream Shop              Pharmacy   
12       Fast Food Restaurant    Gym / Fitness Center     Convenience Store   
13             Ice Cream Shop     Japanese Restaurant                  Park   
14       Caribbean Restaurant           Deli / Bodega    Chinese Restaurant   
17  Latin American Restaurant                  Lounge         Deli / Bodega   
19                Supermarket              Donut Shop         Deli / Bodega   
21                Bus Station     Sporting Goods Shop              Pharmacy   
23         Mexican Restaurant                   Diner              Pharmacy   
25                      Diner                    Park           Bus Station   
28             Farmers Market                    Café    Spanish Restaurant   
31                Supermarket          Sandwich Place    Mexican Restaurant   
32          Food & Drink Shop           Deli / Bodega            Playground   
33                       Park           Deli / Bodega              Pharmacy   
34                  Nightclub    Caribbean Restaurant           Event Space   
35        Fried Chicken Joint          Mattress Store           Bus Station   
36         Frozen Yogurt Shop          Ice Cream Shop           Coffee Shop   
37                      Diner       Food & Drink Shop              Platform   
38              Deli 

#### Cluster 4

In [197]:
bronx_merged.loc[bronx_merged['Cluster Labels'] == 3, bronx_merged.columns[[0] + list(range(4, bronx_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
3  Country Club        Sandwich Place                   Spa   

  3rd Most Common Venue        4th Most Common Venue 5th Most Common Venue  \
3            Playground  Eastern European Restaurant           Fish Market   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
3     Fish & Chips Shop           Film Studio  Fast Food Restaurant   

  9th Most Common Venue 10th Most Common Venue  
3        Farmers Market            Event Space

#### Cluster 5

In [196]:
bronx_merged.loc[bronx_merged['Cluster Labels'] == 4, bronx_merged.columns[[0] + list(range(4, bronx_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
29  Fieldston                 Plaza           Bus Station   

   3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
29                 River         Women's Store  Eastern European Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
29     Fish & Chips Shop           Film Studio  Fast Food Restaurant   

   9th Most Common Venue 10th Most Common Venue  
29        Farmers Market            Event Space

Here we can see that there is a cluster that is more common that the other ones, In this specific cluster that is the number 3 in our k-means procedure, we can see that most of this venues are pizza places, bodegas or delis, banks and finally different kinds of restaurants but mostly Italian restaurants, there are other similitudes but most neighborhoods in the Bronx have this characteristics.

We can finally visualize the cluster of neighborhoods in Bronx, lets continue with Brooklyn

# Explore Neighborhoods in Brooklyn

In [70]:
brooklyn_venues = getNearbyVenues(names=brooklyndf['Name'],
                                   latitudes=brooklyndf['Latitude'],
                                   longitudes=brooklyndf['Longitude'],
                              )

East Williamsburg
Spring Creek
Georgetown
Prospect Park South
Midwood
North Side
Bergen Beach
City Line
Ocean Hill
Prospect Lefferts Gardens
Boerum Hill
Downtown
Sea Gate
South Side
Navy Yard
Rugby
Fort Hamilton
Clinton Hill
Homecrest
Dumbo
Broadway Junction
Weeksville
Vinegar Hill
Ocean Parkway
Fulton Ferry
Paerdegat Basin
New Lots
Remsen Village
Wingate
Ditmas Park
Highland Park
Mill Basin
Marine Park
Madison
Dyker Heights
Bensonhurst
Sunset Park
Bay Ridge
Williamsburg
Windsor Terrace
Kensington
East Flatbush
Crown Heights
Flatbush
Manhattan Terrace
Sheepshead Bay
Bushwick
Brighton Beach
Greenpoint
Gravesend
Prospect Heights
Brownsville
Bedford Stuyvesant
Brooklyn Heights
Borough Park
Bath Beach
Coney Island
Manhattan Beach
Mill Island
Flatlands
Canarsie
Gerritsen Beach
Starrett City
Cypress Hills
Park Slope
Fort Greene
Gowanus
Red Hook
Carroll Gardens
Cobble Hill
East New York


### Let's check the size of the resulting dataframe

In [71]:
print(brooklyn_venues.shape)
brooklyn_venues.head()

(2767, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  East Williamsburg              40.708492              -73.938858   
1  East Williamsburg              40.708492              -73.938858   
2  East Williamsburg              40.708492              -73.938858   
3  East Williamsburg              40.708492              -73.938858   
4  East Williamsburg              40.708492              -73.938858   

                Venue  Venue Latitude  Venue Longitude  \
0           The Topaz       40.707327       -73.939754   
1        Champs Diner       40.708335       -73.940816   
2  Dun-Well Doughnuts       40.707429       -73.940260   
3            The Well       40.708455       -73.937747   
4             Newtown       40.709153       -73.937147   

                  Venue Category  
0                   Cocktail Bar  
1  Vegetarian / Vegan Restaurant  
2                     Donut Shop  
3                            Bar  
4                           Café

In [72]:
brooklyn_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Bath Beach                                    48                      48   
Bay Ridge                                     85                      85   
Bedford Stuyvesant                            28                      28   
Bensonhurst                                   33                      33   
Bergen Beach                                   6                       6   
Boerum Hill                                  100                     100   
Borough Park                                  22                      22   
Brighton Beach                                45                      45   
Broadway Junction                             17                      17   
Brooklyn Heights                             100                     100   
Brownsville                                   21                      21   
Bushwick                                      72                      72   
Canarsie                                       7                       7   
Carroll Gardens                               55                      55   
City Line                                     32                      32   
Clinton Hill                                  98                      98   
Cobble Hill                                  100                     100   
Coney Island                                  17                      17   
Crown Heights                                 22                      22   
Cypress Hills                                 14                      14   
Ditmas Park                                   50                      50   
Downtown                                     100                     100   
Dumbo                                         68                      68   
Dyker Heights                                  6                       6   
East Flatbush                                 12                      12   
East New York                                 14                      14   
East Williamsburg                             69                      69   
Flatbush                                      19                      19   
Flatlands                                     19                      19   
Fort Greene                                   68                      68   
Fort Hamilton                                 72                      72   
Fulton Ferry                                  58                      58   
Georgetown                                    29                      29   
Gerritsen Beach                               20                      20   
Gowanus                                       62                      62   
Gravesend                                     26                      26   
Greenpoint                                   100                     100   
Highland Park                                 12                      12   
Homecrest                                     36                      36   
Kensington                                    36                      36   
Madison                                       11                      11   
Manhattan Beach                               10                      10   
Manhattan Terrace                             21                      21   
Marine Park                                   11                      11   
Midwood                                       13                      13   
Mill Basin                                    33                      33   
Mill Island                                    1                       1   
Navy Yard                                     32                      32   
New Lots                                      19                      19   
North Side                                   100                     100   
Ocean Hill                                    28                      28   

Let's find out how many unique categories can be curated from all the returned venues

In [73]:
print('There are {} uniques categories.'.format(len(brooklyn_venues['Venue Category'].unique())))

There are 293 uniques categories.


## Analyze Each Neighborhood Brooklyn

In [74]:
brooklyn_onehot = pd.get_dummies(brooklyn_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
brooklyn_onehot['Neighborhood'] = brooklyn_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [brooklyn_onehot.columns[-1]] + list(brooklyn_onehot.columns[:-1])
brooklyn_onehot = brooklyn_onehot[fixed_columns]

brooklyn_onehot.head()

Yoga Studio  Accessories Store  Airport Terminal  American Restaurant  \
0            0                  0                 0                    0   
1            0                  0                 0                    0   
2            0                  0                 0                    0   
3            0                  0                 0                    0   
4            0                  0                 0                    0   

   Antique Shop  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0             0                 0                       0            0   
1             0                 0                       0            0   
2             0                 0                       0            0   
3             0                 0                       0            0   
4             0                 0                       0            0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auto Dealership  Auto Garage  Auto Workshop  BBQ Joint  \
0                   0                0            0              0          0   
1                   0                0            0              0          0   
2                   0                0            0              0          0   
3                   0                0            0              0          0   
4                   0                0            0              0          0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    1               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Beach  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0                 0      0         0            0           0              0   
1                 0      0         0            0           0              0   
2                 0      0         0            0           0              0   
3                 0      0         0            0           0              0   
4                 0      0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  \
0              0          0         0           0                     0   
1              0          0         0           0                     0   
2              0          0         0           0                     0   
3              0          0         0           0                     0   
4              0          0         0           0                     0   

   Breakfast Spot  Brewery  Bridal Shop  Bridge  Bubble Tea Shop  Buffet  \
0               0        0            0       0                0       0   
1               0        0            0       0                0       0   
2               0        0            0       0                0       0   
3               0        0            0       0                0       0   
4               0        0            0

And let's examine the new dataframe size.

In [75]:
brooklyn_onehot.shape

(2767, 293)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [76]:
brooklyn_grouped = brooklyn_onehot.groupby('Neighborhood').mean().reset_index()
brooklyn_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                  Bath Beach     0.000000           0.000000   
1                   Bay Ridge     0.000000           0.000000   
2          Bedford Stuyvesant     0.000000           0.000000   
3                 Bensonhurst     0.000000           0.000000   
4                Bergen Beach     0.000000           0.000000   
5                 Boerum Hill     0.020000           0.000000   
6                Borough Park     0.000000           0.000000   
7              Brighton Beach     0.000000           0.000000   
8           Broadway Junction     0.000000           0.000000   
9            Brooklyn Heights     0.040000           0.000000   
10                Brownsville     0.000000           0.000000   
11                   Bushwick     0.000000           0.000000   
12                   Canarsie     0.000000           0.000000   
13            Carroll Gardens     0.036364           0.000000   
14                  City Line     0.000000           0.000000   
15               Clinton Hill     0.030612           0.000000   
16                Cobble Hill     0.030000           0.000000   
17               Coney Island     0.000000           0.000000   
18              Crown Heights     0.000000           0.000000   
19              Cypress Hills     0.000000           0.000000   
20                Ditmas Park     0.020000           0.000000   
21                   Downtown     0.010000           0.000000   
22                      Dumbo     0.014706           0.000000   
23              Dyker Heights     0.000000           0.000000   
24              East Flatbush     0.000000           0.000000   
25              East New York     0.000000           0.000000   
26          East Williamsburg     0.000000           0.000000   
27                   Flatbush     0.000000           0.000000   
28                  Flatlands     0.000000           0.000000   
29                Fort Greene     0.014706           0.000000   
30              Fort Hamilton     0.000000           0.000000   
31               Fulton Ferry     0.000000           0.000000   
32                 Georgetown     0.000000           0.000000   
33            Gerritsen Beach     0.000000           0.000000   
34                    Gowanus     0.016129           0.000000   
35                  Gravesend     0.000000           0.000000   
36                 Greenpoint     0.030000           0.000000   
37              Highland Park     0.000000           0.000000   
38                  Homecrest     0.000000           0.000000   
39                 Kensington     0.000000           0.000000   
40                    Madison     0.000000           0.000000   
41            Manhattan Beach     0.000000           0.000000   
42          Manhattan Terrace     0.000000           0.000000   
43                Marine Park     0.000000           0.000000   
44                    Midwood     0.000000           0.000000   
45                 Mill Basin     0.000000           0.000000   
46                Mill Island     0.000000           0.000000   
47                  Navy Yard     0.000000           0.000000   
48                   New Lots     0.000000           0.000000   
49                 North Side     0.020000           0.000000   
50                 Ocean Hill     0.000000           0.000000   
51              Ocean Parkway     0.000000           0.000000   
52            Paerdegat Basin     0.000000           0.000000   
53                 Park Slope     0.014706           0.014706   
54           Prospect Heights     0.011905           0.000000   
55  Prospect Lefferts Gardens     0.000000           0.000000   
56        Prospect Park South     0.000000           0.000000   
57                   Red Hook     0.000000           0.000000   
58             Remsen Village     0.000000           0.000000   
59                      Rugby     0.000000           0.000000   
60                   Sea Gate     0.000000          

Lets check the size again

In [77]:
brooklyn_grouped.shape

(71, 293)

#### Let's print each neighborhood along with the top 5 most common venues

In [78]:
num_top_venues = 5

for hood in brooklyn_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = brooklyn_grouped[brooklyn_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Bath Beach----
                  venue  freq
0              Pharmacy  0.06
1    Chinese Restaurant  0.06
2       Bubble Tea Shop  0.04
3  Fast Food Restaurant  0.04
4    Italian Restaurant  0.04


----Bay Ridge----
                 venue  freq
0                  Spa  0.06
1   Italian Restaurant  0.06
2          Pizza Place  0.06
3  American Restaurant  0.04
4     Greek Restaurant  0.04


----Bedford Stuyvesant----
           venue  freq
0  Deli / Bodega  0.11
1    Coffee Shop  0.07
2            Bar  0.07
3           Café  0.07
4    Pizza Place  0.07


----Bensonhurst----
                venue  freq
0         Pizza Place  0.09
1          Donut Shop  0.06
2  Chinese Restaurant  0.06
3    Sushi Restaurant  0.06
4      Ice Cream Shop  0.06


----Bergen Beach----
                venue  freq
0     Harbor / Marina  0.33
1          Playground  0.17
2  Athletics & Sports  0.17
3          Donut Shop  0.17
4      Baseball Field  0.17


----Boerum Hill----
               venue  freq
0        C

                   venue  freq
0                   Pool   1.0
1            Yoga Studio   0.0
2           Optical Shop   0.0
3           Outlet Store   0.0
4  Outdoors & Recreation   0.0


----Navy Yard----
           venue  freq
0    Film Studio  0.16
1    Coffee Shop  0.12
2  Historic Site  0.03
3     Bagel Shop  0.03
4            Spa  0.03


----New Lots----
                 venue  freq
0        Grocery Store  0.11
1  Fried Chicken Joint  0.11
2          Pizza Place  0.11
3   Chinese Restaurant  0.05
4     Asian Restaurant  0.05


----North Side----
                 venue  freq
0          Coffee Shop  0.09
1          Pizza Place  0.06
2               Bakery  0.03
3  American Restaurant  0.03
4             Wine Bar  0.03


----Ocean Hill----
                             venue  freq
0                    Deli / Bodega  0.18
1                    Grocery Store  0.11
2                Convenience Store  0.07
3                         Bus Stop  0.07
4  Southern / Soul Food Restaurant  0.07



#### Let's put that into a pandas dataframe

Let's use the function to sort the venues in descending order and let's create the new dataframe and display the top 10 venues for each neighborhood.

In [79]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedBrook = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedBrook['Neighborhood'] = brooklyn_grouped['Neighborhood']

for ind in np.arange(brooklyn_grouped.shape[0]):
    neighborhoods_venues_sortedBrook.iloc[ind, 1:] = return_most_common_venues(brooklyn_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedBrook.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Bath Beach              Pharmacy    Chinese Restaurant   
1           Bay Ridge           Pizza Place                   Spa   
2  Bedford Stuyvesant         Deli / Bodega                  Café   
3         Bensonhurst           Pizza Place    Chinese Restaurant   
4        Bergen Beach       Harbor / Marina    Athletics & Sports   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0  Fast Food Restaurant           Gas Station    Italian Restaurant   
1    Italian Restaurant                   Bar      Greek Restaurant   
2           Pizza Place                   Bar           Coffee Shop   
3        Ice Cream Shop            Donut Shop    Italian Restaurant   
4            Playground            Donut Shop        Baseball Field   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0       Bubble Tea Shop           Coffee Shop   Rental Car Location   
1   American Restaurant    Chinese Restaurant            Playground   
2              Tiki Bar             Gift Shop          Gourmet Shop   
3      Sushi Restaurant         Grocery Store                   Spa   
4         Women's Store         Event Service           Event Space   

      9th Most Common Venue     10th Most Common Venue  
0          Sushi Restaurant                  Surf Spot  
1  Mediterranean Restaurant  Middle Eastern Restaurant  
2   New American Restaurant                 Bagel Shop  
3                    Bakery        Sporting Goods Shop  
4                   Factory         Falafel Restaurant

# Clustering of the neighborhoods of Brooklyn

Run k-means to cluster the neighborhood into 5 clusters.

In [80]:
# set number of clusters
kclusters = 5

brooklyn_grouped_clustering = brooklyn_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(brooklyn_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 3, 3, 3, 0, 3, 3, 3, 3, 3], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [81]:
#neighborhoods_venues_sortedBrooklyn.drop(['Cluster Labels'], axis = 1, inplace = True) If you get the error that clusters are alredy inserted uncomment this.
#neighborhoods_venues_sortedBrooklyn.head()

In [82]:
# add clustering labels
neighborhoods_venues_sortedBrook.insert(0, 'Cluster Labels', kmeans.labels_)

brooklyn_merged = brooklyndf

# merge brooklyn_merged with broolyndf to add latitude/longitude for each neighborhood
brooklyn_merged = brooklyn_merged.join(neighborhoods_venues_sortedBrook.set_index('Neighborhood'), on='Name')

brooklyn_merged.head() # check the last columns!

Name   Latitude  Longitude  Cluster Labels  \
0    East Williamsburg  40.708492 -73.938858               3   
1         Spring Creek  40.657139 -73.869988               3   
2           Georgetown  40.623845 -73.916075               3   
3  Prospect Park South  40.647009 -73.962613               3   
4              Midwood  40.625596 -73.957595               3   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                   Bar         Deli / Bodega          Cocktail Bar   
1        Discount Store         Women's Store            Kids Store   
2                  Bank              Pharmacy        Breakfast Spot   
3  Caribbean Restaurant           Pizza Place         Grocery Store   
4           Pizza Place        Ice Cream Shop      Video Game Store   

  4th Most Common Venue 5th Most Common Venue      6th Most Common Venue  \
0           Coffee Shop                Bakery                Music Venue   
1        Hardware Store         Shopping Mall                 Shoe Store   
2            Donut Shop    Mexican Restaurant             Shipping Store   
3  Fast Food Restaurant     Mobile Phone Shop  Latin American Restaurant   
4                 Field           Candy Store          Electronics Store   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0          Concert Hall    Mexican Restaurant            Donut Shop   
1          Burger Joint           Pizza Place     Mobile Phone Shop   
2           Supermarket    Frozen Yogurt Shop    Miscellaneous Shop   
3   Fried Chicken Joint            Donut Shop    Mexican Restaurant   
4              Pharmacy                Bakery         Moving Target   

          10th Most Common Venue  
0  Vegetarian / Vegan Restaurant  
1           Caribbean Restaurant  
2                  Shopping Mall  
3                  Women's Store  
4              Convenience Store

Let's visualize the resulting clusters

In [83]:
# create map
map_clustersBrook = folium.Map(location=[latitudeb, longitudeb], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(brooklyn_merged['Latitude'], brooklyn_merged['Longitude'], brooklyn_merged['Name'], brooklyn_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersBrook)
       
map_clustersBrook

## Examine Clusters of Brooklyn

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

#### Cluster 1

In [195]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 0, brooklyn_merged.columns[[0] + list(range(4, brooklyn_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
6  Bergen Beach       Harbor / Marina    Athletics & Sports   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
6            Playground            Donut Shop        Baseball Field   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
6         Women's Store         Event Service           Event Space   

  9th Most Common Venue 10th Most Common Venue  
6               Factory     Falafel Restaurant

#### Cluster 2

In [194]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 1, brooklyn_merged.columns[[0] + list(range(4, brooklyn_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
34      Dyker Heights         Grocery Store            Playground   
44  Manhattan Terrace           Pizza Place            Donut Shop   
57    Manhattan Beach                  Café              Bus Stop   
61    Gerritsen Beach                   Bar          Skating Rink   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
34            Bagel Shop          Burger Joint           Golf Course   
44        Ice Cream Shop            Bagel Shop        Cosmetics Shop   
57            Playground        Ice Cream Shop                  Food   
61           Event Space     Martial Arts Dojo           Gas Station   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
34          Dance Studio           Flower Shop           Fish Market   
44     Convenience Store           Coffee Shop       Organic Grocery   
57        Sandwich Place                 Beach       Harbor / Marina   
61                  Café        Baseball Field            Restaurant   

   9th Most Common Venue 10th Most Common Venue  
34     Fish & Chips Shop                   Food  
44            Steakhouse          Grocery Store  
57         Women's Store                   Farm  
61         Grocery Store             Bagel Shop

#### Cluster 3

In [193]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 2, brooklyn_merged.columns[[0] + list(range(4, brooklyn_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
58  Mill Island                  Pool            Food Stand   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
58  Ethiopian Restaurant         Event Service           Event Space   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
58               Factory    Falafel Restaurant                  Farm   

   9th Most Common Venue 10th Most Common Venue  
58        Farmers Market   Fast Food Restaurant

#### Cluster 4

In [192]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 3, brooklyn_merged.columns[[0] + list(range(4, brooklyn_merged.shape[1]))]]

Name 1st Most Common Venue  \
0           East Williamsburg                   Bar   
1                Spring Creek        Discount Store   
2                  Georgetown                  Bank   
3         Prospect Park South  Caribbean Restaurant   
4                     Midwood           Pizza Place   
5                  North Side           Coffee Shop   
7                   City Line            Donut Shop   
8                  Ocean Hill         Deli / Bodega   
9   Prospect Lefferts Gardens                Bakery   
10                Boerum Hill           Coffee Shop   
11                   Downtown          Burger Joint   
12                   Sea Gate                   Spa   
13                 South Side                   Bar   
14                  Navy Yard           Film Studio   
16              Fort Hamilton    Chinese Restaurant   
17               Clinton Hill           Pizza Place   
18                  Homecrest                  Bank   
19                      Dumbo                  Park   
20          Broadway Junction           Bus Station   
21                 Weeksville          Liquor Store   
22               Vinegar Hill            Food Truck   
23              Ocean Parkway     Jewish Restaurant   
24               Fulton Ferry                  Park   
25            Paerdegat Basin                   Gym   
26                   New Lots           Pizza Place   
29                Ditmas Park         Deli / Bodega   
30              Highland Park         Grocery Store   
31                 Mill Basin           Pizza Place   
32                Marine Park        Ice Cream Shop   
33                    Madison            Bagel Shop   
35                Bensonhurst           Pizza Place   
36                Sunset Park                Bakery   
37                  Bay Ridge           Pizza Place   
38               Williamsburg           Coffee Shop   
39            Windsor Terrace         Deli / Bodega   
40                 Kensington         Grocery Store   
42              Crown Heights           Pizza Place   
43                   Flatbush  Caribbean Restaurant   
45             Sheepshead Bay          Dessert Shop   
46                   Bushwick                   Bar   
47             Brighton Beach                 Beach   
48                 Greenpoint                   Bar   
49                  Gravesend           Pizza Place   
50           Prospect Heights                   Bar   
51                Brownsville            Restaurant   
52         Bedford Stuyvesant         Deli / Bodega   
53           Brooklyn Heights           Yoga Studio   
54               Borough Park                  Bank   
55                 Bath Beach              Pharmacy   
60                   Canarsie                   Gym   
62              Starrett City        Cosmetics Shop   
63              Cypress Hills   Fried Chicken Joint   
64                 Park Slope           Coffee Shop   
65                Fort Greene    Italian Restaurant   
66                    Gowanus                   Bar   
67                   Red Hook    Seafood Restaurant   
68            Carroll Gardens                Bakery   
69                Cobble Hill            Playground   
70              East New York         Deli / Bodega   

          2nd Most Common Venue   3rd Most Common Venue  \
0                 Deli / Bodega            Cocktail Bar   
1                 Women's Store              Kids Store   
2                      Pharmacy          Breakfast Spot   
3                   Pizza Place           Grocery Store   
4                Ice Cream Shop        Video Game Store   
5                   Pizza Place     American Restaurant   
7           Fried Chicken Joint           Grocery Store   
8                 Grocery Store      Chinese Restaurant   
9                          Café    Caribbean Restaurant   
10                          Bar  Furniture / Home Store   
11                  Coffee Shop             Pizza Place   
12              

#### Cluster 5

In [191]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 4, brooklyn_merged.columns[[0] + list(range(4, brooklyn_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
15           Rugby  Caribbean Restaurant         Grocery Store   
27  Remsen Village  Caribbean Restaurant  Fast Food Restaurant   
28         Wingate   Fried Chicken Joint         Deli / Bodega   
41   East Flatbush  Caribbean Restaurant              Pharmacy   
56    Coney Island  Caribbean Restaurant   Monument / Landmark   
59       Flatlands              Pharmacy   Fried Chicken Joint   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
15                  Bank    Salon / Barbershop        Sandwich Place   
27           Supermarket            Donut Shop       Auto Dealership   
28                 Field           Bus Station                  Park   
41  Fast Food Restaurant           Supermarket         Moving Target   
56      Baseball Stadium                  Park    Athletics & Sports   
59  Fast Food Restaurant  Caribbean Restaurant                   Bar   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
15           Pizza Place           Wings Joint     Mobile Phone Shop   
27        Sandwich Place   Fried Chicken Joint        Discount Store   
28  Gym / Fitness Center             BBQ Joint    Chinese Restaurant   
41                  Park    Chinese Restaurant        Hardware Store   
56          Skating Rink           Music Venue        Farmers Market   
59        Discount Store           Video Store     Electronics Store   

   9th Most Common Venue 10th Most Common Venue  
15              Pharmacy                  Diner  
27        Breakfast Spot               Pharmacy  
28            Donut Shop              Juice Bar  
41     Food & Drink Shop             Print Shop  
56                 Beach             Food Court  
59             Nightclub                 Lounge

 In the Brooklyn clusters we can see that there is a cluster that is more common that the other ones, In this specific cluster that is the number 4 in our k-means procedure, we can see that most of this venues are different kinds of restaurants, banks, grocery stores, actually there is a big variety of shops in this cluster, there are other similitudes but most neighborhoods in Brooklyn have this characteristics.

We can finally visualize the cluster of neighborhoods in Bronx, lets continue with Manhattan

# Explore Neighborhoods in Manhattan

In [89]:
manhattan_venues = getNearbyVenues(names=manhdf['Name'],
                                   latitudes=manhdf['Latitude'],
                                   longitudes=manhdf['Longitude'],
                              )

Flatiron
Civic Center
Tudor City
Turtle Bay
Sutton Place
Midtown South
Noho
Carnegie Hill
Stuyvesant Town
Marble Hill
West Village
Clinton
Upper East Side
East Harlem
Central Harlem
Manhattanville
Roosevelt Island
Upper West Side
Lincoln Square
Financial District
Midtown
Murray Hill
Hamilton Heights
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Inwood
Little Italy
Soho
Manhattan Valley
Morningside Heights
Gramercy
Washington Heights
Battery Park City
Chinatown
Lenox Hill
Yorkville


Let's check the size of the resulting dataframe

In [90]:
print(manhattan_venues.shape)
manhattan_venues.head()

(3176, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0     Flatiron              40.739673              -73.990947   
1     Flatiron              40.739673              -73.990947   
2     Flatiron              40.739673              -73.990947   
3     Flatiron              40.739673              -73.990947   
4     Flatiron              40.739673              -73.990947   

               Venue  Venue Latitude  Venue Longitude          Venue Category  
0  The Fhitting Room       40.739857       -73.993194                     Gym  
1         Fishs Eddy       40.738605       -73.990017  Furniture / Home Store  
2         sweetgreen       40.738061       -73.991223             Salad Place  
3     SoulCycle 19th       40.739434       -73.992168            Cycle Studio  
4     Five Iron Golf       40.738959       -73.991544             Sports Club

In [91]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       82                      82     82   
Carnegie Hill                           92                      92     92   
Central Harlem                          42                      42     42   
Chelsea                                100                     100    100   
Chinatown                              100                     100    100   
Civic Center                           100                     100    100   
Clinton                                100                     100    100   
East Harlem                             41                      41     41   
East Village                           100                     100    100   
Financial District                     100                     100    100   
Flatiron                               100                     100    100   
Gramercy                                93                      93     93   
Greenwich Village                      100                     100    100   
Hamilton Heights                        60                      60     60   
Inwood                                  57                      57     57   
Lenox Hill                             100                     100    100   
Lincoln Square                         100                     100    100   
Little Italy                           100                     100    100   
Lower East Side                         51                      51     51   
Manhattan Valley                        49                      49     49   
Manhattanville                          44                      44     44   
Marble Hill                             26                      26     26   
Midtown                                100                     100    100   
Midtown South                          100                     100    100   
Morningside Heights                     40                      40     40   
Murray Hill                            100                     100    100   
Noho                                   100                     100    100   
Roosevelt Island                        29                      29     29   
Soho                                   100                     100    100   
Stuyvesant Town                         19                      19     19   
Sutton Place                           100                     100    100   
Tribeca                                 94                      94     94   
Tudor City                              76                      76     76   
Turtle Bay                             100                     100    100   
Upper East Side                         98                      98     98   
Upper West Side                         93                      93     93   
Washington Heights                      90                      90     90   
West Village                           100                     100    100   
Yorkville                              100                     100    100   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City                82               82              82  
Carnegie Hill                    92               92              92  
Central Harlem                   42               42              42  
Chelsea                         100              100             100  
Chinatown                       100              100             100  
Civic Center                    100              100             100  
Clinton                         100              100             100  
East Harlem                      41               41              41  
East Village                    100              100             100  
Financial District              100              100             100  
Flatiron   

Let's find out how many unique categories can be curated from all the returned venues

In [92]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 324 uniques categories.


## Analyze Each Neighborhood of Manhattan

In [93]:
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  Accessories Store  Acupuncturist  Adult Boutique  \
0     Flatiron                  0              0               0   
1     Flatiron                  0              0               0   
2     Flatiron                  0              0               0   
3     Flatiron                  0              0               0   
4     Flatiron                  0              0               0   

   Afghan Restaurant  African Restaurant  American Restaurant  Antique Shop  \
0                  0                   0                    0             0   
1                  0                   0                    0             0   
2                  0                   0                    0             0   
3                  0                   0                    0             0   
4                  0                   0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0                    0                 0                   0           0   
1                    0                 0                   0           0   
2                    0                 0                   0           0   
3                    0                 0                   0           0   
4                    0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  BBQ Joint  Baby Store  \
0                      0                    0          0           0   
1                      0                    0          0           0   
2                      0                    0          0           0   
3                      0                    0          0           0   
4                      0                    0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Basketball Court  Beer Bar  \
0           0       0     0    0               0                 0         0   
1           0       0     0    0               0                 0         0   
2           0       0     0    0               0                 0         0   
3           0       0     0    0               0                 0         0   
4           0       0     0    0               0                 0         0   

   Beer Garden  Beer Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  \
0            0           0                         0          0           0   
1            0           0                         0          0           0   
2            0           0                         0          0           0   
3            0           0                         0          0           0   
4            0           0                         0          0           0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  Boxing Gym  \
0       0           0              0          0         0           0   
1       0           0              0          0         0           0   
2       0           0              0          0         0           0   
3       0           0              0          0         0           0   
4       0           0              0          0         0           0   

   Brazilian Restaurant  Breakfast Spot  Bridal Shop  Bridge  Bubble Tea Shop  \
0                     0               0            0       0                0   
1                     0               0            0       0                0   
2                     0               0            0       0                0   
3                     0     

And let's examine the new dataframe size.

In [94]:
manhattan_onehot.shape

(3176, 325)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [95]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Accessories Store  Acupuncturist  Adult Boutique  \
0     Battery Park City           0.000000           0.00            0.00   
1         Carnegie Hill           0.000000           0.00            0.00   
2        Central Harlem           0.000000           0.00            0.00   
3               Chelsea           0.000000           0.00            0.00   
4             Chinatown           0.000000           0.00            0.00   
5          Civic Center           0.000000           0.00            0.00   
6               Clinton           0.000000           0.00            0.00   
7           East Harlem           0.000000           0.00            0.00   
8          East Village           0.000000           0.00            0.00   
9    Financial District           0.010000           0.00            0.00   
10             Flatiron           0.000000           0.01            0.00   
11             Gramercy           0.000000           0.00            0.00   
12    Greenwich Village           0.000000           0.00            0.00   
13     Hamilton Heights           0.000000           0.00            0.00   
14               Inwood           0.000000           0.00            0.00   
15           Lenox Hill           0.000000           0.00            0.00   
16       Lincoln Square           0.000000           0.00            0.00   
17         Little Italy           0.000000           0.00            0.00   
18      Lower East Side           0.000000           0.00            0.00   
19     Manhattan Valley           0.000000           0.00            0.00   
20       Manhattanville           0.000000           0.00            0.00   
21          Marble Hill           0.000000           0.00            0.00   
22              Midtown           0.000000           0.00            0.00   
23        Midtown South           0.000000           0.00            0.00   
24  Morningside Heights           0.000000           0.00            0.00   
25          Murray Hill           0.000000           0.00            0.00   
26                 Noho           0.000000           0.00            0.00   
27     Roosevelt Island           0.000000           0.00            0.00   
28                 Soho           0.010000           0.00            0.00   
29      Stuyvesant Town           0.000000           0.00            0.00   
30         Sutton Place           0.000000           0.00            0.01   
31              Tribeca           0.000000           0.00            0.00   
32           Tudor City           0.000000           0.00            0.00   
33           Turtle Bay           0.000000           0.00            0.00   
34      Upper East Side           0.000000           0.00            0.00   
35      Upper West Side           0.010753           0.00            0.00   
36   Washington Heights           0.011111           0.00            0.00   
37         West Village           0.000000           0.00            0.00   
38            Yorkville           0.000000           0.00            0.00   

    Afghan Restaurant  African Restaurant  American Restaurant  Antique Shop  \
0                0.00            0.000000             0.012195          0.00   
1                0.00            0.000000             0.010870          0.00   
2                0.00            0.071429             0.047619          0.00   
3                0.00            0.000000             0.040000          0.00   
4                0.00            0.000000             0.040000          0.00   
5                0.00            0.000000             0.030000          0.01   
6                0.00            0.000000             0.040000          0.00   
7                0.00            0.000000             0.000000          0.00   
8                0.00            0.000000             0.020000          0.00   
9                0.00            0.000000             0.050000          0.00   
10               0.00            0.000000         

Lets check the size again

In [96]:
manhattan_grouped.shape

(39, 325)

Let's print each neighborhood along with the top 5 most common venues

In [97]:
num_top_venues = 5

for hood in manhattan_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
            venue  freq
0            Park  0.07
1     Coffee Shop  0.06
2           Hotel  0.06
3   Memorial Site  0.04
4  Clothing Store  0.04


----Carnegie Hill----
                 venue  freq
0          Coffee Shop  0.07
1                 Café  0.05
2            Bookstore  0.03
3               Bakery  0.03
4  Japanese Restaurant  0.03


----Central Harlem----
                 venue  freq
0   African Restaurant  0.07
1   Chinese Restaurant  0.05
2  American Restaurant  0.05
3   Seafood Restaurant  0.05
4    French Restaurant  0.05


----Chelsea----
                 venue  freq
0          Coffee Shop  0.07
1               Bakery  0.04
2  American Restaurant  0.04
3   Italian Restaurant  0.04
4                Hotel  0.03


----Chinatown----
                   venue  freq
0     Chinese Restaurant  0.08
1           Cocktail Bar  0.05
2    American Restaurant  0.04
3  Vietnamese Restaurant  0.03
4      Hotpot Restaurant  0.03


----Civic Center----
            

#### Let's put that into a pandas dataframe

Let's use the function to sort the venues in descending order and let's create the new dataframe and display the top 10 venues for each neighborhood.

In [98]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedManh = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedManh['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sortedManh.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedManh.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City                  Park           Coffee Shop   
1      Carnegie Hill           Coffee Shop                  Café   
2     Central Harlem    African Restaurant    Seafood Restaurant   
3            Chelsea           Coffee Shop   American Restaurant   
4          Chinatown    Chinese Restaurant          Cocktail Bar   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                 Hotel         Boat or Ferry         Memorial Site   
1           Pizza Place   Japanese Restaurant             Bookstore   
2   American Restaurant    Chinese Restaurant     French Restaurant   
3    Italian Restaurant                Bakery                 Hotel   
4   American Restaurant                Bakery    Salon / Barbershop   

  6th Most Common Venue            7th Most Common Venue  \
0        Clothing Store                              Gym   
1        Cosmetics Shop                           Bakery   
2                   Bar  Southern / Soul Food Restaurant   
3        Ice Cream Shop                      Art Gallery   
4          Dessert Shop                              Spa   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0             Food Court         Shopping Mall         Sandwich Place  
1      French Restaurant                   Gym              Wine Shop  
2            Event Space                   Gym               Beer Bar  
3      French Restaurant   Japanese Restaurant                 Market  
4  Vietnamese Restaurant          Optical Shop      Hotpot Restaurant

# Clustering of the neighborhoods of Brooklyn

Run k-means to cluster the neighborhood into 5 clusters.

In [99]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 1, 1, 1, 1, 1, 2, 1, 1], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [100]:
#neighborhoods_venues_sortedManh.drop(['Cluster Labels'], axis = 1, inplace = True) #If you get the error that clusters are alredy inserted uncomment this.
#neighborhoods_venues_sortedManh.head()

In [101]:
# add clustering labels
neighborhoods_venues_sortedManh.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhdf

# merge manhattan_merged with manhdf to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sortedManh.set_index('Neighborhood'), on='Name')

manhattan_merged.head() # check the last columns!

Name   Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
0      Flatiron  40.739673 -73.990947               1           Yoga Studio   
1  Civic Center  40.715229 -74.005415               1           Coffee Shop   
2    Tudor City  40.746917 -73.971219               2                  Park   
3    Turtle Bay  40.752042 -73.967708               1    Italian Restaurant   
4  Sutton Place  40.760280 -73.963556               1    Italian Restaurant   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0   Japanese Restaurant  Gym / Fitness Center                   Spa   
1                 Hotel  Gym / Fitness Center                   Spa   
2                  Café    Mexican Restaurant           Coffee Shop   
3      Sushi Restaurant           Coffee Shop              Wine Bar   
4  Gym / Fitness Center                   Gym           Coffee Shop   

  5th Most Common Venue     6th Most Common Venue  \
0   American Restaurant  Mediterranean Restaurant   
1          Cocktail Bar         French Restaurant   
2         Deli / Bodega          Greek Restaurant   
3            Steakhouse         French Restaurant   
4   American Restaurant         Indian Restaurant   

           7th Most Common Venue    8th Most Common Venue  \
0  Vegetarian / Vegan Restaurant  New American Restaurant   
1            American Restaurant           Sandwich Place   
2                          Diner         Asian Restaurant   
3            Japanese Restaurant                     Park   
4         Furniture / Home Store                     Park   

  9th Most Common Venue 10th Most Common Venue  
0                  Café           Cycle Studio  
1           Yoga Studio                   Park  
2       Thai Restaurant       Sushi Restaurant  
3                  Café                  Hotel  
4           Beer Garden     Chinese Restaurant

Let's visualize the resulting clusters

In [102]:
# create map
map_clustersManh = folium.Map(location=[latitudem, longitudem], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Name'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersManh)
       
map_clustersManh

## Examine Clusters of Manhattan

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

#### Cluster 1

In [190]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[0] + list(range(4, manhattan_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
22  Hamilton Heights           Pizza Place                  Café   
31  Manhattan Valley     Indian Restaurant                   Bar   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
22           Coffee Shop         Deli / Bodega    Mexican Restaurant   
31           Coffee Shop    Mexican Restaurant    Chinese Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
22           Yoga Studio      Sushi Restaurant  Caribbean Restaurant   
31       Thai Restaurant           Pizza Place           Yoga Studio   

   9th Most Common Venue 10th Most Common Venue  
22                Bakery                 School  
31               Dog Run                   Café

#### Cluster 2

In [189]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[0] + list(range(4, manhattan_merged.shape[1]))]]

Name 1st Most Common Venue    2nd Most Common Venue  \
0             Flatiron           Yoga Studio      Japanese Restaurant   
1         Civic Center           Coffee Shop                    Hotel   
3           Turtle Bay    Italian Restaurant         Sushi Restaurant   
4         Sutton Place    Italian Restaurant     Gym / Fitness Center   
5        Midtown South     Korean Restaurant      Japanese Restaurant   
6                 Noho    Italian Restaurant        French Restaurant   
7        Carnegie Hill           Coffee Shop                     Café   
10        West Village    Italian Restaurant  New American Restaurant   
11             Clinton               Theater     Gym / Fitness Center   
12     Upper East Side           Coffee Shop       Italian Restaurant   
14      Central Harlem    African Restaurant       Seafood Restaurant   
17     Upper West Side    Italian Restaurant                 Wine Bar   
18      Lincoln Square                 Plaza       Italian Restaurant   
19  Financial District           Coffee Shop                      Bar   
20             Midtown                 Hotel      Sporting Goods Shop   
21         Murray Hill           Coffee Shop           Sandwich Place   
23             Chelsea           Coffee Shop      American Restaurant   
24   Greenwich Village    Italian Restaurant         Sushi Restaurant   
25        East Village                   Bar              Pizza Place   
26     Lower East Side    Chinese Restaurant                     Café   
27             Tribeca   American Restaurant                     Park   
29        Little Italy                  Café                   Bakery   
30                Soho        Clothing Store       Italian Restaurant   
33            Gramercy                   Bar       Italian Restaurant   
35   Battery Park City                  Park              Coffee Shop   
36           Chinatown    Chinese Restaurant             Cocktail Bar   
37          Lenox Hill    Italian Restaurant              Coffee Shop   
38           Yorkville    Italian Restaurant                      Gym   

   3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
0   Gym / Fitness Center                   Spa    American Restaurant   
1   Gym / Fitness Center                   Spa           Cocktail Bar   
3            Coffee Shop              Wine Bar             Steakhouse   
4                    Gym           Coffee Shop    American Restaurant   
5                  Hotel          Dessert Shop            Coffee Shop   
6                  Hotel          Cocktail Bar            Coffee Shop   
7            Pizza Place   Japanese Restaurant              Bookstore   
10   American Restaurant             Jazz Club                   Park   
11    Italian Restaurant             Wine Shop    American Restaurant   
12               Exhibit                Bakery   Gym / Fitness Center   
14   American Restaurant    Chinese Restaurant      French Restaurant   
17                   Bar                Bakery                   Café   
18               Theater                  Café  Performing Arts Venue   
19   American Restaurant           Pizza Place           Cocktail Bar   
20           Coffee Shop            Steakhouse         Clothing Store   
21   American Restaurant   Japanese Restaurant                  Hotel   
23    Italian Restaurant                Bakery                  Hotel   
24        Clothing Store                  Café      French Restaurant   
25        Ice Cream Shop          Cocktail Bar     Mexican Restaurant   
26           Coffee Shop   Japanese Restaurant                 Bakery   
27    Italian Restaurant                  Café                    Spa   
29       Bubble Tea Shop                 Hotel     Italian Restaurant   
30              Boutique           Coffee Shop                  Hotel   
33           Pizza Place            Bagel Shop    American Restaurant   
35                 Hotel         Boat or Ferry          Memorial Site   
36

#### Cluster 3

In [188]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[0] + list(range(4, manhattan_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
2            Tudor City                  Park                  Café   
13          East Harlem    Mexican Restaurant       Thai Restaurant   
15       Manhattanville           Coffee Shop    Seafood Restaurant   
16     Roosevelt Island                  Park         Indie Theater   
28               Inwood                  Café    Mexican Restaurant   
32  Morningside Heights                  Park           Coffee Shop   
34   Washington Heights                  Café                Bakery   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2     Mexican Restaurant           Coffee Shop         Deli / Bodega   
13                Bakery           Pizza Place         Deli / Bodega   
15   Fried Chicken Joint         Deli / Bodega    Mexican Restaurant   
16           Dry Cleaner           Supermarket         Metro Station   
28            Restaurant           Pizza Place                Lounge   
32   American Restaurant             Bookstore         Deli / Bodega   
34         Grocery Store    Chinese Restaurant     Mobile Phone Shop   

        6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
2            Greek Restaurant                 Diner      Asian Restaurant   
13  Latin American Restaurant              Beer Bar           Gas Station   
15                       Park    Italian Restaurant          Music School   
16             Farmers Market              Bus Line           Bus Station   
28         Frozen Yogurt Shop    Chinese Restaurant         Deli / Bodega   
32               Burger Joint        Sandwich Place           Supermarket   
34               Liquor Store           Pizza Place           Supermarket   

   9th Most Common Venue 10th Most Common Venue  
2        Thai Restaurant       Sushi Restaurant  
13          Liquor Store             Taco Place  
15   Dumpling Restaurant                   Bank  
16          Soccer Field    Monument / Landmark  
28              Wine Bar                   Park  
32        Farmers Market            Salad Place  
34       Supplement Shop         Sandwich Place

#### Cluster 4

In [187]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[0] + list(range(4, manhattan_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
8  Stuyvesant Town         Boat or Ferry                   Bar   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
8                  Park           Pet Service        Baseball Field   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
8  Gym / Fitness Center          Cocktail Bar           Coffee Shop   

  9th Most Common Venue 10th Most Common Venue  
8       Harbor / Marina            Gas Station

#### Cluster 5

In [186]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[0] + list(range(4, manhattan_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
9  Marble Hill        Sandwich Place   American Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
9                   Gym           Coffee Shop           Yoga Studio   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
9        Discount Store    Miscellaneous Shop           Pizza Place   

  9th Most Common Venue 10th Most Common Venue  
9            Steakhouse          Shopping Mall

The Manhattan cluster have a cluster that is more common that the other ones, In this specific cluster that is the number 2 in our k-means procedure, we can see that most of this venues are Italian, Korean, Japanese restaurants mostly Italian, coffee shops and gym or fitness centers, there are other similitudes but most neighborhoods in Manhattan have this characteristics.

We can finally visualize the cluster of neighborhoods in Manhattan, lets continue with Queens.

## Explore Neighborhoods in Queens

In [108]:
queens_venues = getNearbyVenues(names=queendf['Name'],
                                   latitudes=queendf['Latitude'],
                                   longitudes=queendf['Longitude'],
                              )

Queensboro Hill
Somerville
Rockaway Park
Belle Harbor
Lefrak City
Lindenwood
Ravenswood
Hillcrest
Brookville
Bellaire
Middle Village
Forest Hills Gardens
Jamaica Hills
Utopia
Pomonok
Astoria Heights
Hunters Point
Sunnyside Gardens
Blissville
Roxbury
Jamaica Estates
Malba
North Corona
Holliswood
Laurelton
Murray Hill
Whitestone
Bayside
Auburndale
Little Neck
Douglaston
Glen Oaks
Bellerose
Kew Gardens Hills
Fresh Meadows
Briarwood
Jamaica Center
Oakland Gardens
Queens Village
Floral Park
Hollis
College Point
South Ozone Park
Woodhaven
Rego Park
Astoria
Woodside
Jackson Heights
Elmhurst
Howard Beach
South Corona
Forest Hills
South Jamaica
Kew Gardens
Downtown Flushing
Long Island City
Sunnyside
East Elmhurst
Maspeth
Ridgewood
Glendale
Richmond Hill
St. Albans
Ozone Park
Rosedale
Neponsit
Rochdale
Springfield Gardens
Cambria Heights
Seaside
Arverne
Edgemere
Far Rockaway
Broad Channel
Breezy Point
Bay Terrace
Beechhurst
Steinway


Let's check the size of the resulting dataframe

In [109]:
print(queens_venues.shape)
queens_venues.head()

(2113, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Queensboro Hill              40.744572              -73.825809   
1  Queensboro Hill              40.744572              -73.825809   
2  Queensboro Hill              40.744572              -73.825809   
3  Queensboro Hill              40.744572              -73.825809   
4  Queensboro Hill              40.744572              -73.825809   

                                Venue  Venue Latitude  Venue Longitude  \
0               Kung Fu Xiao Long Bao       40.743380       -73.825741   
1                     Yeh's Bakery 紅葉       40.745714       -73.825912   
2          New Bodai Vegetarian 新菩提素食       40.743630       -73.825807   
3               Tea Shop 168 & Bakery       40.743241       -73.825726   
4  Main Street Taiwanese Gourmet 北港台菜       40.743538       -73.825825   

                  Venue Category  
0            Dumpling Restaurant  
1                         Bakery  
2  Vegetarian / Vegan Restaurant  
3                         Bakery  
4             Chinese Restaurant

In [110]:
queens_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                 
Arverne                                  18                      18     18   
Astoria                                 100                     100    100   
Astoria Heights                          13                      13     13   
Auburndale                               18                      18     18   
Bay Terrace                              37                      37     37   
Bayside                                  74                      74     74   
Beechhurst                               11                      11     11   
Bellaire                                 10                      10     10   
Belle Harbor                             17                      17     17   
Bellerose                                22                      22     22   
Blissville                               19                      19     19   
Breezy Point                              4                       4      4   
Briarwood                                12                      12     12   
Broad Channel                             5                       5      5   
Brookville                                2                       2      2   
Cambria Heights                          13                      13     13   
College Point                            41                      41     41   
Douglaston                               20                      20     20   
Downtown Flushing                       100                     100    100   
East Elmhurst                            10                      10     10   
Edgemere                                 14                      14     14   
Elmhurst                                 32                      32     32   
Far Rockaway                             32                      32     32   
Floral Park                               6                       6      6   
Forest Hills                             39                      39     39   
Forest Hills Gardens                     24                      24     24   
Fresh Meadows                            14                      14     14   
Glen Oaks                                21                      21     21   
Glendale                                  5                       5      5   
Hillcrest                                18                      18     18   
Hollis                                   14                      14     14   
Holliswood                                6                       6      6   
Howard Beach                             38                      38     38   
Hunters Point                            69                      69     69   
Jackson Heights                          80                      80     80   
Jamaica Center                           44                      44     44   
Jamaica Estates                           4                       4      4   
Jamaica Hills                            30                      30     30   
Kew Gardens                              43                      43     43   
Kew Gardens Hills                        20                      20     20   
Laurelton                                 8                       8      8   
Lefrak City                              22                      22     22   
Lindenwood                               12                      12     12   
Little Neck                              48                      48     48   
Long Island City                         70                      70     70   
Malba                                     3                       3      3   
Maspeth                                  33                      33     33   
Middle Village                           16                      16     16   
Murray Hill                              48                      48     48   
Neponsit                                  4 

Let's find out how many unique categories can be curated from all the returned venues

In [111]:
print('There are {} uniques categories.'.format(len(queens_venues['Venue Category'].unique())))

There are 267 uniques categories.


## Analyze Each Neighborhood of Queens

In [112]:
queens_onehot = pd.get_dummies(queens_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
queens_onehot['Neighborhood'] = queens_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [queens_onehot.columns[-1]] + list(queens_onehot.columns[:-1])
queens_onehot = queens_onehot[fixed_columns]

queens_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  American Restaurant  \
0            0                  0                  0                    0   
1            0                  0                  0                    0   
2            0                  0                  0                    0   
3            0                  0                  0                    0   
4            0                  0                  0                    0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auto Workshop  Automotive Shop  BBQ Joint  Bagel Shop  \
0                   0              0                0          0           0   
1                   0              0                0          0           0   
2                   0              0                0          0           0   
3                   0              0                0          0           0   
4                   0              0                0          0           0   

   Bakery  Bank  Bar  Baseball Field  Basketball Court  Bath House  Beach  \
0       0     0    0               0                 0           0      0   
1       1     0    0               0                 0           0      0   
2       0     0    0               0                 0           0      0   
3       1     0    0               0                 0           0      0   
4       0     0    0               0                 0           0      0   

   Beach Bar  Bed & Breakfast  Beer Garden  Bike Trail  Bistro  Board Shop  \
0          0                0            0           0       0           0   
1          0                0            0           0       0           0   
2          0                0            0           0       0           0   
3          0                0            0           0       0           0   
4          0                0            0           0       0           0   

   Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  Breakfast Spot  \
0          0         0              0                     0               0   
1          0         0              0                     0               0   
2          0         0              0                     0               0   
3          0         0              0                     0               0   
4          0         0              0                     0               0   

   Brewery  Bridal Shop  Bubble Tea Shop  Buffet  Burger Joint  Burrito Place  \
0        0            0                0       0             0              0   
1        0            0                0       0             0              0   
2        0            0                0       0             0              0   
3        0            0                0       0             0              0   
4        0            0                0       0             0              0   

   Bus Line  Bus Station  Bus Stop  Business Service  Butcher  Café  \
0         0            0         0                 0        0     0   
1         0            0         0                 0        0     0   
2         0            0         0                 0        0     0   
3         0            0         0                 

And let's examine the new dataframe size.

In [113]:
manhattan_onehot.shape

(3176, 325)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [114]:
queens_grouped = queens_onehot.groupby('Neighborhood').mean().reset_index()
queens_grouped

Neighborhood  Yoga Studio  Accessories Store  Afghan Restaurant  \
0                Arverne     0.000000           0.000000             0.0000   
1                Astoria     0.000000           0.000000             0.0000   
2        Astoria Heights     0.000000           0.000000             0.0000   
3             Auburndale     0.000000           0.000000             0.0000   
4            Bay Terrace     0.000000           0.027027             0.0000   
5                Bayside     0.013514           0.000000             0.0000   
6             Beechhurst     0.000000           0.000000             0.0000   
7               Bellaire     0.000000           0.000000             0.0000   
8           Belle Harbor     0.000000           0.000000             0.0000   
9              Bellerose     0.000000           0.000000             0.0000   
10            Blissville     0.000000           0.000000             0.0000   
11          Breezy Point     0.000000           0.000000             0.0000   
12             Briarwood     0.000000           0.000000             0.0000   
13         Broad Channel     0.000000           0.000000             0.0000   
14            Brookville     0.000000           0.000000             0.0000   
15       Cambria Heights     0.000000           0.000000             0.0000   
16         College Point     0.000000           0.000000             0.0000   
17            Douglaston     0.050000           0.000000             0.0000   
18     Downtown Flushing     0.000000           0.000000             0.0000   
19         East Elmhurst     0.000000           0.000000             0.0000   
20              Edgemere     0.000000           0.000000             0.0000   
21              Elmhurst     0.000000           0.000000             0.0000   
22          Far Rockaway     0.000000           0.000000             0.0000   
23           Floral Park     0.000000           0.000000             0.0000   
24          Forest Hills     0.051282           0.000000             0.0000   
25  Forest Hills Gardens     0.000000           0.000000             0.0000   
26         Fresh Meadows     0.000000           0.000000             0.0000   
27             Glen Oaks     0.000000           0.000000             0.0000   
28              Glendale     0.000000           0.000000             0.0000   
29             Hillcrest     0.000000           0.000000             0.0000   
30                Hollis     0.000000           0.000000             0.0000   
31            Holliswood     0.000000           0.000000             0.0000   
32          Howard Beach     0.000000           0.000000             0.0000   
33         Hunters Point     0.014493           0.000000             0.0000   
34       Jackson Heights     0.000000           0.000000             0.0000   
35        Jamaica Center     0.000000           0.000000             0.0000   
36       Jamaica Estates     0.000000           0.000000             0.0000   
37         Jamaica Hills     0.000000           0.000000             0.0000   
38           Kew Gardens     0.000000           0.000000             0.0000   
39     Kew Gardens Hills     0.000000           0.000000             0.0000   
40             Laurelton     0.000000           0.000000             0.0000   
41           Lefrak City     0.000000           0.000000             0.0000   
42            Lindenwood     0.000000           0.000000             0.0000   
43           Little Neck     0.000000           0.000000             0.0000   
44      Long Island City     0.000000           0.000000             0.0000   
45                 Malba     0.000000           0.000000             0.0000   
46               Maspeth     0.000000           0.000000             0.0000   
47        Middle Village     0.000000           0.000000             0.0000   
48           Murray Hill     0.000000           0.000000             0.0000   
49              Neponsit     0.000000           0.000000      

Lets check the size again

In [115]:
queens_grouped.shape

(78, 267)

Let's print each neighborhood along with the top 5 most common venues

In [116]:
num_top_venues = 5

for hood in queens_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = queens_grouped[queens_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Arverne----
             venue  freq
0        Surf Spot  0.22
1    Metro Station  0.11
2   Sandwich Place  0.11
3       Donut Shop  0.06
4  Thai Restaurant  0.06


----Astoria----
                       venue  freq
0                        Bar  0.07
1                 Hookah Bar  0.06
2  Middle Eastern Restaurant  0.06
3           Greek Restaurant  0.05
4         Seafood Restaurant  0.04


----Astoria Heights----
                venue  freq
0       Deli / Bodega  0.08
1              Bakery  0.08
2         Bus Station  0.08
3  Italian Restaurant  0.08
4               Plaza  0.08


----Auburndale----
                  venue  freq
0    Miscellaneous Shop  0.06
1    Athletics & Sports  0.06
2      Sushi Restaurant  0.06
3  Fast Food Restaurant  0.06
4          Noodle House  0.06


----Bay Terrace----
               venue  freq
0     Clothing Store  0.11
1  Mobile Phone Shop  0.05
2     Cosmetics Shop  0.05
3         Kids Store  0.05
4     Lingerie Store  0.05


----Bayside----
         

                  venue  freq
0           Coffee Shop  0.11
1                 Hotel  0.11
2  Gym / Fitness Center  0.06
3                   Bar  0.06
4           Pizza Place  0.06


----Malba----
                           venue  freq
0  Vegetarian / Vegan Restaurant  0.33
1                      Rest Area  0.33
2                   Tennis Court  0.33
3                    Yoga Studio  0.00
4                   Optical Shop  0.00


----Maspeth----
                venue  freq
0               Diner  0.09
1         Pizza Place  0.09
2       Grocery Store  0.06
3  Chinese Restaurant  0.06
4   Mobile Phone Shop  0.06


----Middle Village----
                venue  freq
0        Dessert Shop  0.06
1              Bakery  0.06
2  Spanish Restaurant  0.06
3          Sports Bar  0.06
4    Sushi Restaurant  0.06


----Murray Hill----
               venue  freq
0  Korean Restaurant  0.48
1        Coffee Shop  0.04
2        Supermarket  0.04
3                Bar  0.04
4               Bank  0.04


----N

#### Let's put that into a pandas dataframe

Let's use the function to sort the venues in descending order and let's create the new dataframe and display the top 10 venues for each neighborhood.

In [117]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedQueens = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedQueens['Neighborhood'] = queens_grouped['Neighborhood']

for ind in np.arange(queens_grouped.shape[0]):
    neighborhoods_venues_sortedQueens.iloc[ind, 1:] = return_most_common_venues(queens_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedQueens.head()

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
0          Arverne             Surf Spot              Metro Station   
1          Astoria                   Bar  Middle Eastern Restaurant   
2  Astoria Heights          Burger Joint                       Food   
3       Auburndale            Hookah Bar         Athletics & Sports   
4      Bay Terrace        Clothing Store              Women's Store   

  3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
0        Sandwich Place           Pizza Place              Playground   
1            Hookah Bar      Greek Restaurant      Seafood Restaurant   
2           Supermarket                Bakery             Bus Station   
3    Miscellaneous Shop     Mobile Phone Shop  Furniture / Home Store   
4            Kids Store            Donut Shop       Mobile Phone Shop   

  6th Most Common Venue     7th Most Common Venue 8th Most Common Venue  \
0             Wine Shop                     Beach            Donut Shop   
1     Indian Restaurant  Mediterranean Restaurant                   Gym   
2    Italian Restaurant             Shopping Mall         Deli / Bodega   
3           Supermarket         Korean Restaurant      Sushi Restaurant   
4            Shoe Store            Lingerie Store        Cosmetics Shop   

  9th Most Common Venue 10th Most Common Venue  
0       Thai Restaurant        Bed & Breakfast  
1     Food & Drink Shop             Food Truck  
2         Bowling Alley                 Hostel  
3          Noodle House     Italian Restaurant  
4   American Restaurant       Video Game Store

## Clustering of the neighborhoods of Queens

Run k-means to cluster the neighborhood into 5 clusters.

In [118]:
# set number of clusters
kclusters = 5

queens_grouped_clustering = queens_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(queens_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([4, 4, 4, 4, 4, 4, 4, 4, 4, 4], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [119]:
#neighborhoods_venues_sortedQueens.drop(['Cluster Labels'], axis = 1, inplace = True) #If you get the error that clusters are alredy inserted uncomment this.
#neighborhoods_venues_sortedQueens.head()

In [120]:
# add clustering labels
neighborhoods_venues_sortedQueens.insert(0, 'Cluster Labels', kmeans.labels_)

queens_merged = queendf

# merge queens_merged with queensdf to add latitude/longitude for each neighborhood
queens_merged = queens_merged.join(neighborhoods_venues_sortedQueens.set_index('Neighborhood'), on='Name')

queens_merged.head() # check the last columns!

Name   Latitude  Longitude  Cluster Labels  \
0  Queensboro Hill  40.744572 -73.825809               4   
1       Somerville  40.597711 -73.796648               1   
2    Rockaway Park  40.580343 -73.841534               4   
3     Belle Harbor  40.576156 -73.854018               4   
4      Lefrak City  40.736075 -73.862525               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0    Chinese Restaurant                  Bank                Bakery   
1                  Park         Women's Store            Eye Doctor   
2                 Beach            Donut Shop            Steakhouse   
3                 Beach         Deli / Bodega                   Pub   
4      Department Store        Cosmetics Shop                Bakery   

         4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                  Bus Station          Intersection   Dumpling Restaurant   
1  Eastern European Restaurant   Egyptian Restaurant     Electronics Store   
2                  Pizza Place                  Bank                   Bar   
3                          Spa            Bagel Shop    Chinese Restaurant   
4                     Pharmacy            Restaurant         Shopping Mall   

    7th Most Common Venue    8th Most Common Venue 9th Most Common Venue  \
0      Frozen Yogurt Shop                      Bar            Bagel Shop   
1     Empanada Restaurant              Event Space    Falafel Restaurant   
2              Bagel Shop      Japanese Restaurant    Seafood Restaurant   
3      Mexican Restaurant                 Boutique    Italian Restaurant   
4  Furniture / Home Store  Fruit & Vegetable Store   Fried Chicken Joint   

  10th Most Common Venue  
0                   Park  
1            Dry Cleaner  
2         Sandwich Place  
3                 Bakery  
4             Steakhouse

Let's visualize the resulting clusters

In [121]:
# create map
map_clustersQueens = folium.Map(location=[latitudeq, longitudeq], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(queens_merged['Latitude'], queens_merged['Longitude'], queens_merged['Name'], queens_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersQueens)
       
map_clustersQueens

## Examine Clusters of Queens

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

#### Cluster 1

In [185]:
queens_merged.loc[queens_merged['Cluster Labels'] == 0, queens_merged.columns[[0] + list(range(4, queens_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
8   Brookville        Nightlife Spot         Deli / Bodega   
26  Whitestone           Candy Store       Bubble Tea Shop   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
8          Women's Store    Falafel Restaurant   Egyptian Restaurant   
26          Dance Studio         Deli / Bodega                  Farm   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
8      Electronics Store   Empanada Restaurant           Event Space   
26     Electronics Store   Empanada Restaurant           Event Space   

   9th Most Common Venue 10th Most Common Venue  
8             Eye Doctor                   Farm  
26            Eye Doctor     Falafel Restaurant

#### Cluster 2

In [184]:
queens_merged.loc[queens_merged['Cluster Labels'] == 1, queens_merged.columns[[0] + list(range(4, queens_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
1  Somerville                  Park         Women's Store   

  3rd Most Common Venue        4th Most Common Venue 5th Most Common Venue  \
1            Eye Doctor  Eastern European Restaurant   Egyptian Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
1     Electronics Store   Empanada Restaurant           Event Space   

  9th Most Common Venue 10th Most Common Venue  
1    Falafel Restaurant            Dry Cleaner

#### Cluster 3

In [183]:
queens_merged.loc[queens_merged['Cluster Labels'] == 2, queens_merged.columns[[0] + list(range(4, queens_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
65      Neponsit                 Beach         Women's Store   
74  Breezy Point                 Beach   Monument / Landmark   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
65    Falafel Restaurant   Egyptian Restaurant     Electronics Store   
74                 Trail         Women's Store            Eye Doctor   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
65   Empanada Restaurant           Event Space            Eye Doctor   
74   Egyptian Restaurant     Electronics Store   Empanada Restaurant   

   9th Most Common Venue 10th Most Common Venue  
65                  Farm      Food & Drink Shop  
74           Event Space     Falafel Restaurant

#### Cluster 4

In [182]:
queens_merged.loc[queens_merged['Cluster Labels'] == 3, queens_merged.columns[[0] + list(range(4, queens_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
25  Murray Hill     Korean Restaurant           Coffee Shop   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
25           Supermarket                   Bar                  Bank   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
25           Pet Service             BBQ Joint     Mobile Phone Shop   

   9th Most Common Venue 10th Most Common Venue  
25   Fried Chicken Joint         Breakfast Spot

#### Cluster 5

In [181]:
queens_merged.loc[queens_merged['Cluster Labels'] == 4, queens_merged.columns[[0] + list(range(4, queens_merged.shape[1]))]]

Name            1st Most Common Venue  \
0        Queensboro Hill               Chinese Restaurant   
2          Rockaway Park                            Beach   
3           Belle Harbor                            Beach   
4            Lefrak City                 Department Store   
5             Lindenwood                      Pizza Place   
6             Ravenswood               Chinese Restaurant   
7              Hillcrest                       Donut Shop   
9               Bellaire                    Deli / Bodega   
10        Middle Village                   Sandwich Place   
11  Forest Hills Gardens                           Bakery   
12         Jamaica Hills                Indian Restaurant   
13                Utopia                    Deli / Bodega   
14               Pomonok                      Pizza Place   
15       Astoria Heights                     Burger Joint   
16         Hunters Point                             Café   
17     Sunnyside Gardens                              Bar   
18            Blissville                    Deli / Bodega   
19               Roxbury                        Irish Pub   
20       Jamaica Estates                      Bus Station   
21                 Malba    Vegetarian / Vegan Restaurant   
22          North Corona                    Deli / Bodega   
23            Holliswood                       Playground   
24             Laurelton             Caribbean Restaurant   
27               Bayside                              Bar   
28            Auburndale                       Hookah Bar   
29           Little Neck               Italian Restaurant   
30            Douglaston                    Deli / Bodega   
31             Glen Oaks                         Pharmacy   
32             Bellerose                      Pizza Place   
33     Kew Gardens Hills                             Bank   
34         Fresh Meadows                      Bus Station   
35             Briarwood                    Deli / Bodega   
36        Jamaica Center                   Clothing Store   
37       Oakland Gardens                Korean Restaurant   
38        Queens Village                             Bank   
39           Floral Park                Indian Restaurant   
40                Hollis              Fried Chicken Joint   
41         College Point        Latin American Restaurant   
42      South Ozone Park                    Deli / Bodega   
43             Woodhaven                         Pharmacy   
44             Rego Park                           Bakery   
45               Astoria                              Bar   
46              Woodside                    Grocery Store   
47       Jackson Heights        Latin American Restaurant   
48              Elmhurst                  Thai Restaurant   
49          Howard Beach               Italian Restaurant   
50          South Corona               Mexican Restaurant   
51          Forest Hills             Gym / Fitness Center   
52         South Jamaica                      Bus Station   
53           Kew Gardens               Chinese Restaurant   
54     Downtown Flushing               Chinese Restaurant   
55      Long Island City                            Hotel   
56             Sunnyside                      Pizza Place   
57         East Elmhurst                       Donut Shop   
58               Maspeth                      Pizza Place   
59             Ridgewood                      Pizza Place   
60              Glendale                Food & Drink Shop   
61         Richmond Hill                      Pizza Place   
62            St. Albans             Caribbean Restaurant   
63            Ozone Park                      Pizza Place   
64              Rosedale                      Bus Station   
66              Rochdale  Southern / Soul Food Restaurant   
67   Springfield Gardens                      Bus Station   
68       Cambria Heights             Caribbean Restaurant   
69               Seaside                            Bea

In the Queens cluster have a cluster that is more common that the other ones, In this specific cluster that is the number 5 in our k-means procedure, we can see that most of this venues donuts shops, some Chinese restaurants and deli or bodegas, there are other similitudes but most neighborhoods in Queens have this characteristics.

We can finally visualize the cluster of neighborhoods in Queens, lets finally go with Staten Island

## Explore Neighborhoods in Staten Island

In [127]:
staten_venues = getNearbyVenues(names=statisdf['Name'],
                                   latitudes=statisdf['Latitude'],
                                   longitudes=statisdf['Longitude'],
                              )

Grymes Hill
Todt Hill
South Beach
Port Richmond
Mariner's Harbor
Port Ivory
Castleton Corners
New Springville
West Brighton
Rosebank
Silver Lake
New Brighton
St. George
Travis
Manor Heights
Willowbrook
Sandy Ground
Egbertville
Prince's Bay
Lighthouse Hill
Richmond Valley
Stapleton
New Dorp
Elm Park
Howland Hook
Huguenot
Bay Terrace
New Dorp Beach
Grant City
Midland Beach
Dongan Hills
Old Town
Grasmere
Arrochar
Arlington
Graniteville
Westerleigh
Park Hill
Tottenville
Tompkinsville
Pleasant Plains
Butler Manor
Woodrow
Rossville
Randall Manor
Emerson Hill
Concord
Clifton
Shore Acres
Richmond Town
Oakwood
Sunnyside
Great Kills
Annadale
Bulls Head
Bloomfield
Chelsea
Heartland Village
Greenridge
Arden Heights
Eltingville
Charleston


Let's check the size of the resulting dataframe

In [128]:
print(staten_venues.shape)
staten_venues.head()

(816, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Grymes Hill              40.624185              -74.087248   
1  Grymes Hill              40.624185              -74.087248   
2  Grymes Hill              40.624185              -74.087248   
3  Grymes Hill              40.624185              -74.087248   
4    Todt Hill              40.597069              -74.111329   

                                  Venue  Venue Latitude  Venue Longitude  \
0              Silver Lake Park Dog Run       40.626393       -74.091626   
1  MTA Bus - Targee St & Broad St (S74)       40.623143       -74.083820   
2                 Kennedy Fried Chicken       40.623521       -74.082365   
3  MTA Bus - Targee St & Young St (S74)       40.620722       -74.084303   
4                  St Francis Woodlands       40.599524       -74.114515   

        Venue Category  
0              Dog Run  
1             Bus Stop  
2  American Restaurant  
3             Bus Stop  
4                 Park

In [129]:
staten_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                              
Annadale                              12                      12     12   
Arden Heights                          4                       4      4   
Arlington                              4                       4      4   
Arrochar                              18                      18     18   
Bay Terrace                           10                      10     10   
Bloomfield                             5                       5      5   
Bulls Head                            45                      45     45   
Butler Manor                           6                       6      6   
Castleton Corners                     15                      15     15   
Charleston                            29                      29     29   
Chelsea                                7                       7      7   
Clifton                               20                      20     20   
Concord                                9                       9      9   
Dongan Hills                          24                      24     24   
Egbertville                            5                       5      5   
Elm Park                               9                       9      9   
Eltingville                           45                      45     45   
Emerson Hill                           1                       1      1   
Graniteville                           4                       4      4   
Grant City                            20                      20     20   
Grasmere                              20                      20     20   
Great Kills                           21                      21     21   
Greenridge                             8                       8      8   
Grymes Hill                            4                       4      4   
Heartland Village                     11                      11     11   
Howland Hook                           1                       1      1   
Huguenot                               8                       8      8   
Lighthouse Hill                        5                       5      5   
Manor Heights                          9                       9      9   
Mariner's Harbor                       6                       6      6   
Midland Beach                         12                      12     12   
New Brighton                          13                      13     13   
New Dorp                              23                      23     23   
New Dorp Beach                        12                      12     12   
New Springville                       27                      27     27   
Oakwood                                2                       2      2   
Old Town                              17                      17     17   
Park Hill                              6                       6      6   
Pleasant Plains                       21                      21     21   
Port Ivory                             1                       1      1   
Port Richmond                          5                       5      5   
Prince's Bay                          11                      11     11   
Randall Manor                          5                       5      5   
Richmond Town                          5                       5      5   
Richmond Valley                        9                       9      9   
Rosebank                              26                      26     26   
Rossville                             13                      13     13   
Sandy Ground                           4                       4      4   
Shore Acres                           26                      26     26   
Silver Lake                            4                       4      4   
South Beach                            7                       7      7   
St. George                            34    

Let's find out how many unique categories can be curated from all the returned venues

In [130]:
print('There are {} uniques categories.'.format(len(staten_venues['Venue Category'].unique())))

There are 179 uniques categories.


## Analyze Each Neighborhood of Staten Island

In [131]:
staten_onehot = pd.get_dummies(staten_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
staten_onehot['Neighborhood'] = staten_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [staten_onehot.columns[-1]] + list(staten_onehot.columns[:-1])
staten_onehot = staten_onehot[fixed_columns]

staten_onehot.head()

Neighborhood  American Restaurant  Antique Shop  Arcade  Art Gallery  \
0  Grymes Hill                    0             0       0            0   
1  Grymes Hill                    0             0       0            0   
2  Grymes Hill                    1             0       0            0   
3  Grymes Hill                    0             0       0            0   
4    Todt Hill                    0             0       0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 0   
3          0           0       0     0    0               0                 0   
4          0           0       0     0    0               0                 0   

   Basketball Court  Beach  Beer Bar  Big Box Store  Board Shop  Bookstore  \
0                 0      0         0              0           0          0   
1                 0      0         0              0           0          0   
2                 0      0         0              0           0          0   
3                 0      0         0              0           0          0   
4                 0      0         0              0           0          0   

   Bowling Alley  Breakfast Spot  Brewery  Bridal Shop  Bubble Tea Shop  \
0              0               0        0            0                0   
1              0               0        0            0                0   
2              0               0        0            0                0   
3              0               0        0            0                0   
4              0               0        0            0                0   

   Burger Joint  Bus Line  Bus Stop  Butcher  Café  Cajun / Creole Restaurant  \
0             0         0         0        0     0                          0   
1             0         0         1        0     0                          0   
2             0         0         0        0     0                          0   
3             0         0         1        0     0                          0   
4             0         0         0        0     0                          0   

   Campground  Caribbean Restaurant  Chinese Restaurant  Clothing Store  \
0           0                     0                   0               0   
1           0                     0                   0               0   
2           0                     0                   0               0   
3           0                     0                   0               0   
4           0                     0                   0               0   

   Coffee Shop  Comedy Club  Concert Hall  Construction & Landscaping  \
0            0            0             0                           0   
1            0            0             0                           0   
2            0            0             0                           0   
3            0            0             0                           0   
4            0            0             0                           0   

   Convenience Store  Cosmetics Shop  Dance Studio  Daycare  Deli / Bodega  \
0                  0               0             0        0              0   
1                  0               0             0        0              0   
2                  0               0             0        0              0   
3   

And let's examine the new dataframe size.

In [132]:
staten_onehot.shape

(816, 180)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category¶

In [133]:
staten_grouped = staten_onehot.groupby('Neighborhood').mean().reset_index()
staten_grouped

Neighborhood  American Restaurant  Antique Shop    Arcade  \
0            Annadale             0.083333      0.000000  0.000000   
1       Arden Heights             0.000000      0.000000  0.000000   
2           Arlington             0.000000      0.000000  0.000000   
3            Arrochar             0.000000      0.000000  0.000000   
4         Bay Terrace             0.000000      0.000000  0.000000   
5          Bloomfield             0.000000      0.000000  0.000000   
6          Bulls Head             0.000000      0.000000  0.000000   
7        Butler Manor             0.000000      0.000000  0.000000   
8   Castleton Corners             0.000000      0.000000  0.000000   
9          Charleston             0.034483      0.000000  0.000000   
10            Chelsea             0.000000      0.000000  0.000000   
11            Clifton             0.000000      0.000000  0.000000   
12            Concord             0.000000      0.000000  0.000000   
13       Dongan Hills             0.000000      0.000000  0.000000   
14        Egbertville             0.000000      0.000000  0.000000   
15           Elm Park             0.111111      0.000000  0.000000   
16        Eltingville             0.000000      0.000000  0.000000   
17       Emerson Hill             0.000000      0.000000  0.000000   
18       Graniteville             0.000000      0.000000  0.000000   
19         Grant City             0.000000      0.000000  0.000000   
20           Grasmere             0.000000      0.000000  0.000000   
21        Great Kills             0.000000      0.000000  0.000000   
22         Greenridge             0.000000      0.000000  0.000000   
23        Grymes Hill             0.250000      0.000000  0.000000   
24  Heartland Village             0.000000      0.000000  0.000000   
25       Howland Hook             0.000000      0.000000  0.000000   
26           Huguenot             0.000000      0.000000  0.000000   
27    Lighthouse Hill             0.000000      0.000000  0.000000   
28      Manor Heights             0.111111      0.000000  0.000000   
29   Mariner's Harbor             0.000000      0.000000  0.000000   
30      Midland Beach             0.000000      0.000000  0.000000   
31       New Brighton             0.000000      0.000000  0.000000   
32           New Dorp             0.000000      0.000000  0.000000   
33     New Dorp Beach             0.000000      0.000000  0.000000   
34    New Springville             0.000000      0.000000  0.000000   
35            Oakwood             0.000000      0.000000  0.000000   
36           Old Town             0.058824      0.000000  0.000000   
37          Park Hill             0.000000      0.000000  0.000000   
38    Pleasant Plains             0.000000      0.000000  0.000000   
39         Port Ivory             0.000000      0.000000  0.000000   
40      Port Richmond             0.000000      0.000000  0.000000   
41       Prince's Bay             0.000000      0.000000  0.000000   
42      Randall Manor             0.000000      0.000000  0.000000   
43      Richmond Town             0.000000      0.000000  0.000000   
44    Richmond Valley             0.000000      0.000000  0.000000   
45           Rosebank             0.038462      0.000000  0.000000   
46          Rossville             0.076923      0.000000  0.000000   
47       Sandy Ground             0.000000      0.000000  0.000000   
48        Shore Acres             0.000000      0.000000  0.000000   
49        Silver Lake             0.250000      0.000000  0.000000   
50        South Beach             0.000000      0.000000  0.000000   
51         St. George             0.029412      0.000000  0.000000   
52          Stapleton             0.000000      0.028571  0.000000   
53          Sunnyside             0.142857      0.000000  0.000000   
54          Todt Hill             0.000000      0.000000  0.000000   
55      Tompkinsville             0.000000      0.000000  0.000000   
56        Tottenvil

Lets check the size again

In [134]:
staten_grouped.shape

(62, 180)

Let's print each neighborhood along with the top 5 most common venues

In [135]:
num_top_venues = 5

for hood in staten_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = staten_grouped[staten_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Annadale----
                 venue  freq
0  American Restaurant  0.08
1               Bakery  0.08
2         Dance Studio  0.08
3                  Pub  0.08
4          Pizza Place  0.08


----Arden Heights----
                 venue  freq
0        Deli / Bodega  0.25
1             Pharmacy  0.25
2          Coffee Shop  0.25
3          Pizza Place  0.25
4  American Restaurant  0.00


----Arlington----
                    venue  freq
0           Deli / Bodega  0.25
1           Grocery Store  0.25
2  Furniture / Home Store  0.25
3                Bus Stop  0.25
4     American Restaurant  0.00


----Arrochar----
                       venue  freq
0                   Bus Stop  0.11
1              Deli / Bodega  0.11
2         Italian Restaurant  0.11
3  Middle Eastern Restaurant  0.06
4      Outdoors & Recreation  0.06


----Bay Terrace----
                venue  freq
0         Supermarket   0.2
1  Italian Restaurant   0.2
2       Train Station   0.1
3          Donut Shop   0.1
4  Salon

            venue  freq
0  Sandwich Place  0.11
1   Train Station  0.11
2            Food  0.11
3     Coffee Shop  0.11
4   Smoothie Shop  0.11


----Rosebank----
                 venue  freq
0   Italian Restaurant  0.08
1        Grocery Store  0.08
2  American Restaurant  0.04
3             Pharmacy  0.04
4           Taco Place  0.04


----Rossville----
                 venue  freq
0           Bagel Shop  0.23
1          Pizza Place  0.23
2  American Restaurant  0.08
3        Grocery Store  0.08
4          Dry Cleaner  0.08


----Sandy Ground----
          venue  freq
0  Home Service  0.25
1      Bus Stop  0.25
2        Market  0.25
3  Intersection  0.25
4    Playground  0.00


----Shore Acres----
                venue  freq
0  Italian Restaurant  0.15
1            Bus Stop  0.12
2       Deli / Bodega  0.12
3                 Bar  0.08
4        Intersection  0.08


----Silver Lake----
                 venue  freq
0  American Restaurant  0.25
1              Dog Run  0.25
2         Burge

#### Let's put that into a pandas dataframe

Let's use the function to sort the venues in descending order and let's create the new dataframe and display the top 10 venues for each neighborhood.

In [136]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedStaten = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedStaten['Neighborhood'] = staten_grouped['Neighborhood']

for ind in np.arange(staten_grouped.shape[0]):
    neighborhoods_venues_sortedStaten.iloc[ind, 1:] = return_most_common_venues(staten_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedStaten.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Annadale   American Restaurant                Bakery   
1  Arden Heights         Deli / Bodega              Pharmacy   
2      Arlington         Deli / Bodega         Grocery Store   
3       Arrochar    Italian Restaurant         Deli / Bodega   
4    Bay Terrace    Italian Restaurant           Supermarket   

  3rd Most Common Venue   4th Most Common Venue  5th Most Common Venue  \
0                  Food                    Park               Pharmacy   
1           Coffee Shop             Pizza Place             Food Truck   
2              Bus Stop  Furniture / Home Store         Farmers Market   
3              Bus Stop              Bagel Shop  Outdoors & Recreation   
4         Train Station        Sushi Restaurant           Liquor Store   

  6th Most Common Venue     7th Most Common Venue 8th Most Common Venue  \
0           Pizza Place                     Diner                   Pub   
1     Food & Drink Shop                      Food           Flower Shop   
2     French Restaurant                Food Truck     Food & Drink Shop   
3           Supermarket  Mediterranean Restaurant            Food Truck   
4    Salon / Barbershop                Donut Shop        Shipping Store   

  9th Most Common Venue 10th Most Common Venue  
0            Restaurant             Sports Bar  
1   Filipino Restaurant   Fast Food Restaurant  
2                  Food            Flower Shop  
3        Sandwich Place            Pizza Place  
4    Falafel Restaurant      Food & Drink Shop

## Clustering of the neighborhoods of Staten Island

Run k-means to cluster the neighborhood into 5 clusters.

In [137]:
# set number of clusters
kclusters = 5

staten_grouped_clustering = staten_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(staten_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 2, 0, 0, 2, 0, 0, 0, 0], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [138]:
#neighborhoods_venues_sortedStaten.drop(['Cluster Labels'], axis = 1, inplace = True) #If you get the error that clusters are alredy inserted uncomment this.
#neighborhoods_venues_sortedStaten.head()

In [139]:
# add clustering labels
neighborhoods_venues_sortedStaten.insert(0, 'Cluster Labels', kmeans.labels_)

staten_merged = statisdf

# merge staten_merged with statisdf to add latitude/longitude for each neighborhood
staten_merged = staten_merged.join(neighborhoods_venues_sortedStaten.set_index('Neighborhood'), on='Name').dropna()
staten_merged['Cluster Labels'] = staten_merged['Cluster Labels'].apply(np.int64) #There was a problem with the join function with a neightborhood name that didnt have values so use this to drop and put everything to int again.
staten_merged # check the last columns!

Name   Latitude  Longitude  Cluster Labels  \
0         Grymes Hill  40.624185 -74.087248               2   
1           Todt Hill  40.597069 -74.111329               0   
2         South Beach  40.580247 -74.079553               2   
3       Port Richmond  40.633669 -74.129434               0   
4    Mariner's Harbor  40.632546 -74.150085               2   
5          Port Ivory  40.639683 -74.174645               1   
6   Castleton Corners  40.613336 -74.119181               0   
7     New Springville  40.594252 -74.164960               0   
8       West Brighton  40.631879 -74.107182               0   
9            Rosebank  40.615305 -74.069805               0   
10        Silver Lake  40.619193 -74.096290               0   
11       New Brighton  40.640615 -74.087017               2   
12         St. George  40.644982 -74.079353               0   
13             Travis  40.586314 -74.190737               0   
14      Manor Heights  40.601810 -74.120594               0   
15        Willowbrook  40.603707 -74.132084               2   
16       Sandy Ground  40.541140 -74.217766               2   
17        Egbertville  40.579119 -74.127272               0   
18       Prince's Bay  40.526264 -74.201526               0   
19    Lighthouse Hill  40.576506 -74.137927               0   
20    Richmond Valley  40.519541 -74.229571               0   
21          Stapleton  40.626928 -74.077902               0   
22           New Dorp  40.572572 -74.116479               0   
23           Elm Park  40.630147 -74.141817               2   
24       Howland Hook  40.638433 -74.186223               4   
25           Huguenot  40.531912 -74.191741               0   
26        Bay Terrace  40.553988 -74.139166               0   
27     New Dorp Beach  40.564255 -74.104327               0   
28         Grant City  40.576216 -74.105856               0   
29      Midland Beach  40.573527 -74.093483               0   
30       Dongan Hills  40.588673 -74.096399               0   
31           Old Town  40.596329 -74.087511               0   
32           Grasmere  40.598268 -74.076674               0   
33           Arrochar  40.596313 -74.067124               0   
34          Arlington  40.635325 -74.165104               2   
35       Graniteville  40.620172 -74.153152               2   
36        Westerleigh  40.621090 -74.133041               0   
37          Park Hill  40.609190 -74.080157               2   
38        Tottenville  40.505334 -74.246569               0   
39      Tompkinsville  40.637316 -74.080554               0   
40    Pleasant Plains  40.524699 -74.219831               0   
41       Butler Manor  40.506082 -74.229504               0   
42            Woodrow  40.537453 -74.221351               0   
43          Rossville  40.549404 -74.215729               0   
44      Randall Manor  40.635630 -74.098051               2   
45       Emerson Hill  40.606794 -74.097762               3   
46            Concord  40.604473 -74.084024               0   
47            Clifton  40.619178 -74.072642               0   
48        Shore Acres  40.609719 -74.066678               0   
49      Richmond Town  40.569606 -74.134057               0   
50            Oakwood  40.558462 -74.121566               1   
51          Sunnyside  40.612760 -74.097126               0   
52        Great Kills  40.549480 -74.149324               0   
53           Annadale  40.538114 -74.178549               0   
54         Bulls Head  40.609592 -74.159409               0   
55         Bloomfield  40.605779 -74.187256               2   
56            Chelsea  40.594726 -74.189560               0   
57  Heartland Village  40.589139 -74.159022               0   
58         Greenridge  40.559712 -74.191506               0   
59      Arden Heights  40.549286 -74.185887               0   
60        Eltingville  40.542231 -74.164331               0   
61         Charleston  40.530531 -74.232158               0   

         1st Most Common Venue   2nd Most Commo

Let's visualize the resulting clusters

In [140]:
# create map
map_clustersStaten = folium.Map(location=[latitudest, longitudest], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(staten_merged['Latitude'], staten_merged['Longitude'], staten_merged['Name'], staten_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersStaten)
       
map_clustersStaten

## Examine Clusters of Staten Island

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

#### Cluster 1

In [180]:
staten_merged.loc[staten_merged['Cluster Labels'] == 0, staten_merged.columns[[0] + list(range(4, staten_merged.shape[1]))]]

Name 1st Most Common Venue   2nd Most Common Venue  \
1           Todt Hill                  Park             Yoga Studio   
3       Port Richmond         Deli / Bodega             Pizza Place   
6   Castleton Corners           Pizza Place     Japanese Restaurant   
7     New Springville     Mobile Phone Shop             Coffee Shop   
8       West Brighton           Coffee Shop                Bus Stop   
9            Rosebank    Italian Restaurant           Grocery Store   
10        Silver Lake   American Restaurant             Golf Course   
12         St. George        Clothing Store     Sporting Goods Shop   
13             Travis                 Hotel           Deli / Bodega   
14      Manor Heights         Deli / Bodega              Bagel Shop   
17        Egbertville        Clothing Store      Italian Restaurant   
18       Prince's Bay           Pizza Place              Food Truck   
19    Lighthouse Hill    Italian Restaurant              Art Museum   
20    Richmond Valley         Deli / Bodega          Sandwich Place   
21          Stapleton        Discount Store          Sandwich Place   
22           New Dorp    Italian Restaurant             Pizza Place   
25           Huguenot                  Bank          Sandwich Place   
26        Bay Terrace    Italian Restaurant             Supermarket   
27     New Dorp Beach    Italian Restaurant           Deli / Bodega   
28         Grant City     Convenience Store    Fast Food Restaurant   
29      Midland Beach         Deli / Bodega                   Beach   
30       Dongan Hills         Deli / Bodega             Pizza Place   
31           Old Town    Italian Restaurant     American Restaurant   
32           Grasmere              Bus Stop           Grocery Store   
33           Arrochar    Italian Restaurant           Deli / Bodega   
36        Westerleigh                Arcade             Art Gallery   
38        Tottenville    Italian Restaurant  Thrift / Vintage Store   
39      Tompkinsville           Pizza Place                    Park   
40    Pleasant Plains           Pizza Place                    Bank   
41       Butler Manor                  Pool          Baseball Field   
42            Woodrow          Intersection             Art Gallery   
43          Rossville            Bagel Shop             Pizza Place   
46            Concord         Deli / Bodega    Gym / Fitness Center   
47            Clifton    Mexican Restaurant           Grocery Store   
48        Shore Acres    Italian Restaurant           Deli / Bodega   
49      Richmond Town        History Museum      Italian Restaurant   
51          Sunnyside               Theater     American Restaurant   
52        Great Kills    Italian Restaurant             Pizza Place   
53           Annadale   American Restaurant                  Bakery   
54         Bulls Head              Bus Stop             Pizza Place   
56            Chelsea            Steakhouse      Spanish Restaurant   
57  Heartland Village           Coffee Shop           Shopping Mall   
58         Greenridge    Chinese Restaurant                     Bar   
59      Arden Heights         Deli / Bodega                Pharmacy   
60        Eltingville           Pizza Place        Sushi Restaurant   
61         Charleston        Cosmetics Shop           Big Box Store   

   3rd Most Common Venue       4th Most Common Venue  5th Most Common Venue  \
1            Gas Station           French Restaurant             Food Truck   
3             Donut Shop         Rental Car Location         Ice Cream Shop   
6             Bagel Shop               Grocery Store              Mini Golf   
7            Pizza Place     Health & Beauty Service             Bagel Shop   
8         Ice Cream Shop                        Bank                    Bar   
9    American Restaurant                 Pizza Place         Breakfast Spot   
10          Burger Joint                     Dog Run         Farmers Market   
12                   Bar          Italian Resta

#### Cluster 2

In [179]:
staten_merged.loc[staten_merged['Cluster Labels'] == 1, staten_merged.columns[[0] + list(range(4, staten_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
5   Port Ivory                   Bar           Yoga Studio   
50     Oakwood                Lawyer                   Bar   

   3rd Most Common Venue   4th Most Common Venue   5th Most Common Venue  \
5         Farmers Market  Furniture / Home Store       French Restaurant   
50           Yoga Studio          Farmers Market  Furniture / Home Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
5             Food Truck     Food & Drink Shop                  Food   
50     French Restaurant            Food Truck     Food & Drink Shop   

   9th Most Common Venue 10th Most Common Venue  
5            Flower Shop    Filipino Restaurant  
50                  Food            Flower Shop

#### Cluster 3

In [178]:
staten_merged.loc[staten_merged['Cluster Labels'] == 2, staten_merged.columns[[0] + list(range(4, staten_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
0        Grymes Hill              Bus Stop   American Restaurant   
2        South Beach                 Beach                  Pier   
4   Mariner's Harbor         Deli / Bodega    Italian Restaurant   
11      New Brighton              Bus Stop         Deli / Bodega   
15       Willowbrook              Bus Stop         Deli / Bodega   
16      Sandy Ground          Intersection              Bus Stop   
23          Elm Park              Bus Stop   American Restaurant   
34         Arlington         Deli / Bodega         Grocery Store   
35      Graniteville            Food Truck        Sandwich Place   
37         Park Hill              Bus Stop                 Hotel   
44     Randall Manor              Bus Stop         Deli / Bodega   
55        Bloomfield            Theme Park        Discount Store   

   3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
0                Dog Run          Farmers Market     French Restaurant   
2          Deli / Bodega                Bus Stop    Athletics & Sports   
4               Bus Stop      Falafel Restaurant     French Restaurant   
11                  Park              Playground         Bowling Alley   
15          Intersection                     Spa            Bagel Shop   
16                Market            Home Service           Yoga Studio   
23            Toll Plaza          Ice Cream Shop           Pizza Place   
34              Bus Stop  Furniture / Home Store        Farmers Market   
35              Bus Stop           Grocery Store           Yoga Studio   
37    Athletics & Sports    Gym / Fitness Center           Coffee Shop   
44           Pizza Place              Bagel Shop        Farmers Market   
55              Bus Stop                    Park     Recreation Center   

   6th Most Common Venue   7th Most Common Venue 8th Most Common Venue  \
0             Food Truck       Food & Drink Shop                  Food   
2   Fast Food Restaurant  Furniture / Home Store     French Restaurant   
4             Food Truck       Food & Drink Shop                  Food   
11        Discount Store                 Daycare               Dog Run   
15           Pizza Place      Falafel Restaurant     Food & Drink Shop   
16        Farmers Market       French Restaurant            Food Truck   
23         Deli / Bodega      Chinese Restaurant    Italian Restaurant   
34     French Restaurant              Food Truck     Food & Drink Shop   
35    Falafel Restaurant       Food & Drink Shop                  Food   
37           Yoga Studio          Farmers Market            Food Truck   
44     French Restaurant              Food Truck     Food & Drink Shop   
55                 Diner      Dim Sum Restaurant     French Restaurant   

   9th Most Common Venue 10th Most Common Venue  
0            Flower Shop    Filipino Restaurant  
2             Food Truck      Food & Drink Shop  
4            Flower Shop    Filipino Restaurant  
11                 Diner      French Restaurant  
15                  Food            Flower Shop  
16     Food & Drink Shop                   Food  
23    Athletics & Sports              Gastropub  
34                  Food            Flower Shop  
35           Flower Shop    Filipino Restaurant  
37     Food & Drink Shop                   Food  
44                  Food            Flower Shop  
55            Food Truck      Food & Drink Shop

#### Cluster 4

In [177]:
staten_merged.loc[staten_merged['Cluster Labels'] == 3, staten_merged.columns[[0] + list(range(4, staten_merged.shape[1]))]]

Name       1st Most Common Venue 2nd Most Common Venue  \
45  Emerson Hill  Construction & Landscaping           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
45    Falafel Restaurant     French Restaurant            Food Truck   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
45     Food & Drink Shop                  Food           Flower Shop   

   9th Most Common Venue 10th Most Common Venue  
45   Filipino Restaurant   Fast Food Restaurant

#### Cluster 5

In [176]:
staten_merged.loc[staten_merged['Cluster Labels'] == 4, staten_merged.columns[[0] + list(range(4, staten_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
24  Howland Hook    Italian Restaurant           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
24    Falafel Restaurant     French Restaurant            Food Truck   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
24     Food & Drink Shop                  Food           Flower Shop   

   9th Most Common Venue 10th Most Common Venue  
24   Filipino Restaurant   Fast Food Restaurant

In the borough of Staten Island cluster have a cluster that is more common that the other ones, In this specific cluster that is the number 1 in our k-means procedure, we can see that most of this venues coffee shops, some restaurants, mostly Chinese and American ones, there are other similitudes but most neighborhoods in Staten Island have this characteristics.

Now that we have the clustering of each of the neighborhoods in each borough lets do one of all New York.

## Explore Neighborhoods in all of New York

In [146]:
frames = [bronx_grouped, brooklyn_grouped, manhattan_grouped, queens_grouped, staten_grouped]

ny_grouped = pd.concat(frames, sort = True)

In [147]:
ny_grouped.head()

Accessories Store  Acupuncturist  Adult Boutique  Afghan Restaurant  \
0                0.0            NaN             NaN                NaN   
1                0.0            NaN             NaN                NaN   
2                0.0            NaN             NaN                NaN   
3                0.0            NaN             NaN                NaN   
4                0.0            NaN             NaN                NaN   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                 0.0               NaN             0.000000           0.0   
1                 0.0               NaN             0.000000           0.0   
2                 0.0               NaN             0.010000           0.0   
3                 0.0               NaN             0.000000           0.0   
4                 0.0               NaN             0.037037           0.0   

     Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0  0.043478               0.0                     NaN     0.000000   
1  0.000000               0.0                     NaN     0.000000   
2  0.000000               0.0                     NaN     0.000000   
3  0.000000               0.0                     NaN     0.000000   
4  0.000000               0.0                     NaN     0.037037   

   Art Museum  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0         0.0                  NaN                   NaN               0.0   
1         0.0                  NaN                   NaN               0.0   
2         0.0                  NaN                   NaN               0.0   
3         0.0                  NaN                   NaN               0.0   
4         0.0                  NaN                   NaN               0.0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                 0.0         NaN                    NaN                  NaN   
1                 0.0         NaN                    NaN                  NaN   
2                 0.0         NaN                    NaN                  NaN   
3                 0.0         NaN                    NaN                  NaN   
4                 0.0         NaN                    NaN                  NaN   

   Auto Dealership  Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  \
0              NaN          NaN            NaN              NaN        0.0   
1              NaN          NaN            NaN              NaN        0.0   
2              NaN          NaN            NaN              NaN        0.0   
3              NaN          NaN            NaN              NaN        0.0   
4              NaN          NaN            NaN              NaN        0.0   

   Baby Store  Bagel Shop    Bakery      Bank       Bar  Baseball Field  \
0         NaN         0.0  0.000000  0.043478  0.000000        0.000000   
1         NaN         0.0  0.027027  0.000000  0.027027        0.027027   
2         NaN         0.0  0.050000  0.030000  0.020000        0.000000   
3         NaN         0.0  0.000000  0.111111  0.000000        0.000000   
4         NaN         0.0  0.000000  0.037037  0.037037        0.037037   

   Baseball Stadium  Basketball Court  Bath House  Beach  Beach Bar  \
0               NaN               0.0         NaN    NaN        NaN   
1               NaN               0.0         NaN    NaN        NaN   
2               NaN               0.0         NaN    NaN        NaN   
3               NaN               0.0         NaN    NaN        NaN   
4               NaN               0.0         NaN    NaN        NaN   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0              NaN       0.0          NaN         NaN            NaN   
1              NaN       0.0          NaN         NaN            NaN   
2              NaN       0.0          NaN         NaN            NaN   
3              NaN       0.0          NaN         NaN            NaN   
4    

Let´s fill the NaN values with 0 to work with this data.

In [148]:
ny_grouped.fillna(0, inplace = True)

Lets check the size

In [149]:
ny_grouped.shape

(299, 426)

In [150]:
# move neighborhood column to the first column
ny_grouped = ny_grouped[ ['Neighborhood'] + [ col for col in ny_grouped.columns if col != 'Neighborhood' ] ]

In [151]:
ny_grouped.head()

Neighborhood  Accessories Store  Acupuncturist  Adult Boutique  \
0    Baychester                0.0            0.0             0.0   
1  Bedford Park                0.0            0.0             0.0   
2       Belmont                0.0            0.0             0.0   
3   Castle Hill                0.0            0.0             0.0   
4   City Island                0.0            0.0             0.0   

   Afghan Restaurant  African Restaurant  Airport Terminal  \
0                0.0                 0.0               0.0   
1                0.0                 0.0               0.0   
2                0.0                 0.0               0.0   
3                0.0                 0.0               0.0   
4                0.0                 0.0               0.0   

   American Restaurant  Antique Shop    Arcade  Arepa Restaurant  \
0             0.000000           0.0  0.043478               0.0   
1             0.000000           0.0  0.000000               0.0   
2             0.010000           0.0  0.000000               0.0   
3             0.000000           0.0  0.000000               0.0   
4             0.037037           0.0  0.000000               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                     0.0     0.000000         0.0                  0.0   
1                     0.0     0.000000         0.0                  0.0   
2                     0.0     0.000000         0.0                  0.0   
3                     0.0     0.000000         0.0                  0.0   
4                     0.0     0.037037         0.0                  0.0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                   0.0               0.0                 0.0         0.0   
1                   0.0               0.0                 0.0         0.0   
2                   0.0               0.0                 0.0         0.0   
3                   0.0               0.0                 0.0         0.0   
4                   0.0               0.0                 0.0         0.0   

   Australian Restaurant  Austrian Restaurant  Auto Dealership  Auto Garage  \
0                    0.0                  0.0              0.0          0.0   
1                    0.0                  0.0              0.0          0.0   
2                    0.0                  0.0              0.0          0.0   
3                    0.0                  0.0              0.0          0.0   
4                    0.0                  0.0              0.0          0.0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  \
0            0.0              0.0        0.0         0.0         0.0   
1            0.0              0.0        0.0         0.0         0.0   
2            0.0              0.0        0.0         0.0         0.0   
3            0.0              0.0        0.0         0.0         0.0   
4            0.0              0.0        0.0         0.0         0.0   

     Bakery      Bank       Bar  Baseball Field  Baseball Stadium  \
0  0.000000  0.043478  0.000000        0.000000               0.0   
1  0.027027  0.000000  0.027027        0.027027               0.0   
2  0.050000  0.030000  0.020000        0.000000               0.0   
3  0.000000  0.111111  0.000000        0.000000               0.0   
4  0.000000  0.037037  0.037037        0.037037               0.0   

   Basketball Court  Bath House  Beach  Beach Bar  Bed & Breakfast  Beer Bar  \
0               0.0         0.0    0.0        0.0              0.0       0.0   
1               0.0         0.0    0.0        0.0              0.0       0.0   
2               0.0         0.0    0.0        0.0              0.0       0.0   
3               0.0         0.0    0.0        0.0              0.0       0.0   
4               0.0         0.0    0.0        0.0              0.0       0.0   

   Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0          0.0   

In [152]:
num_top_venues = 5

for hood in ny_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = ny_grouped[ny_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Baychester----
                venue  freq
0          Donut Shop  0.09
1  Mexican Restaurant  0.04
2       Boat or Ferry  0.04
3      Mattress Store  0.04
4      Sandwich Place  0.04


----Bedford Park----
                venue  freq
0               Diner  0.11
1       Deli / Bodega  0.08
2  Chinese Restaurant  0.08
3         Pizza Place  0.08
4         Bus Station  0.08


----Belmont----
                venue  freq
0  Italian Restaurant  0.18
1         Pizza Place  0.09
2       Deli / Bodega  0.08
3              Bakery  0.05
4          Donut Shop  0.03


----Castle Hill----
           venue  freq
0    Pizza Place  0.22
1       Pharmacy  0.11
2           Bank  0.11
3  Deli / Bodega  0.11
4    Bus Station  0.11


----City Island----
                    venue  freq
0         Harbor / Marina  0.11
1      Seafood Restaurant  0.07
2  Thrift / Vintage Store  0.07
3                    Park  0.07
4             Music Venue  0.04


----Claremont Village----
            venue  freq
0   Grocer

            venue  freq
0     Bus Station  0.13
1        Bus Stop  0.09
2  Scenic Lookout  0.04
3      Playground  0.04
4            Park  0.04


----Westchester Square----
                  venue  freq
0  Fast Food Restaurant  0.09
1            Donut Shop  0.06
2        Sandwich Place  0.06
3           Pizza Place  0.06
4              Pharmacy  0.06


----Williamsbridge----
                  venue  freq
0             Nightclub  0.25
1            Soup Place  0.25
2                   Bar  0.25
3  Caribbean Restaurant  0.25
4   Peruvian Restaurant  0.00


----Woodlawn----
               venue  freq
0                Pub  0.12
1        Pizza Place  0.12
2      Deli / Bodega  0.08
3  Food & Drink Shop  0.08
4         Playground  0.08


----Bath Beach----
                  venue  freq
0    Chinese Restaurant  0.06
1              Pharmacy  0.06
2           Gas Station  0.04
3  Fast Food Restaurant  0.04
4       Bubble Tea Shop  0.04


----Bay Ridge----
                 venue  freq
0          

            venue  freq
0        Bus Stop   0.2
1            Café   0.2
2            Food   0.1
3      Playground   0.1
4  Ice Cream Shop   0.1


----Manhattan Terrace----
               venue  freq
0        Pizza Place  0.19
1         Donut Shop  0.14
2     Ice Cream Shop  0.10
3     Cosmetics Shop  0.05
4  Mobile Phone Shop  0.05


----Marine Park----
                venue  freq
0  Athletics & Sports  0.09
1        Intersection  0.09
2    Basketball Court  0.09
3         Pizza Place  0.09
4      Ice Cream Shop  0.09


----Midwood----
         venue  freq
0  Pizza Place  0.31
1        Field  0.08
2  Candy Store  0.08
3     Pharmacy  0.08
4       Bakery  0.08


----Mill Basin----
                 venue  freq
0  Japanese Restaurant  0.09
1          Pizza Place  0.09
2       Cosmetics Shop  0.06
3   Chinese Restaurant  0.06
4                 Bank  0.06


----Mill Island----
                 venue  freq
0                 Pool   1.0
1    Accessories Store   0.0
2    Outdoor Sculpture   0.0

ValueError: Length mismatch: Expected axis has 3 elements, new values have 2 elements

There is a problem with the foursquare API with the neighborhood Chelsea, we can still work but be aware that you will se two Chelsea rows.

#### Let's put that into a pandas dataframe

Let's use the function to sort the venues in descending order and let's create the new dataframe and display the top 10 venues for each neighborhood.

In [153]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedNY = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedNY['Neighborhood'] = ny_grouped['Neighborhood']

for ind in np.arange(ny_grouped.shape[0]):
    neighborhoods_venues_sortedNY.iloc[ind, 1:] = return_most_common_venues(ny_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedNY.head()

Neighborhood 1st Most Common Venue   2nd Most Common Venue  \
0    Baychester            Donut Shop           Moving Target   
1  Bedford Park                 Diner             Pizza Place   
2       Belmont    Italian Restaurant             Pizza Place   
3   Castle Hill           Pizza Place                    Bank   
4   City Island       Harbor / Marina  Thrift / Vintage Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0  Other Great Outdoors  Gym / Fitness Center             Pet Store   
1           Bus Station         Deli / Bodega    Chinese Restaurant   
2         Deli / Bodega                Bakery                  Bank   
3                  Park                Market         Deli / Bodega   
4    Seafood Restaurant                  Park        Baseball Field   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0         Boat or Ferry    Mexican Restaurant                  Bank   
1        Sandwich Place    Mexican Restaurant         Grocery Store   
2         Grocery Store            Donut Shop    Mexican Restaurant   
3                 Diner              Pharmacy           Bus Station   
4              Pharmacy                   Bar            Smoke Shop   

  9th Most Common Venue 10th Most Common Venue  
0           Supermarket         Discount Store  
1                  Park                    Gym  
2          Dessert Shop            Coffee Shop  
3           Event Space             Eye Doctor  
4        History Museum            Music Venue

## Clustering of the neighborhoods of New York

Run k-means to cluster the neighborhood into 5 clusters.

In [154]:
# set number of clusters, set more clusters to see more diference.
kclusters = 8

ny_grouped_clustering = ny_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ny_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([2, 2, 0, 2, 2, 2, 5, 2, 2, 2], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [155]:
#neighborhoods_venues_sortedNY.drop(['Cluster Labels'], axis = 1, inplace = True) #If you get the error that clusters are alredy inserted uncomment this.
#neighborhoods_venues_sortedNY.head()

In [156]:
neighborhoods_venues_sortedNY.shape

(299, 11)

In [157]:
# add clustering labels
neighborhoods_venues_sortedNY.insert(0, 'Cluster Labels', kmeans.labels_)

ny_merged = nydf

# merge ny_merged with nydf to add latitude/longitude for each neighborhood
ny_merged = ny_merged.join(neighborhoods_venues_sortedNY.set_index('Neighborhood'), on='Name').dropna()
ny_merged['Cluster Labels'] = ny_merged['Cluster Labels'].apply(np.int64) #There was a problem with the join function with a neightborhood name that didnt have values so use this to drop and put everything to int again.
ny_merged # check the last columns!

Borough                       Name   Latitude  Longitude  \
0            Bronx                  Wakefield  40.894705 -73.847201   
1            Bronx               Clason Point  40.806551 -73.854144   
2            Bronx                Throgs Neck  40.815109 -73.816350   
3            Bronx               Country Club  40.844246 -73.824099   
4            Bronx                Parkchester  40.837938 -73.856003   
5            Bronx         Westchester Square  40.840619 -73.842194   
6            Bronx                   Van Nest  40.843608 -73.866299   
7            Bronx                Morris Park  40.847549 -73.850402   
8            Bronx                    Belmont  40.857277 -73.888452   
9            Bronx             Spuyten Duyvil  40.881395 -73.917190   
10           Bronx            North Riverdale  40.908543 -73.904531   
11           Bronx                  Soundview  40.821012 -73.865746   
12           Bronx                 Pelham Bay  40.850641 -73.832074   
13           Bronx             Edgewater Park  40.821986 -73.813885   
14           Bronx                  Olinville  40.871371 -73.863324   
15           Bronx             Pelham Gardens  40.862966 -73.841612   
16           Bronx                  Concourse  40.834284 -73.915589   
17           Bronx                  Unionport  40.829774 -73.850535   
18           Bronx                   Edenwald  40.884561 -73.848083   
19           Bronx                 Mount Hope  40.848842 -73.908299   
20           Bronx                 Mount Eden  40.843826 -73.916556   
21           Bronx          Concourse Village  40.824780 -73.915847   
22           Bronx          Claremont Village  40.831428 -73.901199   
23           Bronx              Schuylerville  40.826580 -73.826203   
24           Bronx                 Morrisania  40.823592 -73.901506   
25           Bronx                Castle Hill  40.819014 -73.848027   
26           Bronx                   Longwood  40.815099 -73.895788   
27           Bronx                 Co-op City  40.874294 -73.829939   
28           Bronx                Hunts Point  40.809730 -73.883315   
29           Bronx                  Fieldston  40.895437 -73.905643   
30           Bronx                  Riverdale  40.890834 -73.912585   
31           Bronx                Kingsbridge  40.881687 -73.902818   
32           Bronx                   Woodlawn  40.898273 -73.867315   
33           Bronx                    Norwood  40.877224 -73.879391   
34           Bronx             Williamsbridge  40.881039 -73.857446   
35           Bronx                 Baychester  40.866858 -73.835798   
36           Bronx             Pelham Parkway  40.857413 -73.854756   
37           Bronx                Eastchester  40.887556 -73.827806   
38           Bronx               Bedford Park  40.870185 -73.885512   
39           Bronx                    Melrose  40.819754 -73.909422   
40           Bronx               High  Bridge  40.836623 -73.926102   
41           Bronx                 Mott Haven  40.806239 -73.916100   
42           Bronx                 West Farms  40.839475 -73.877745   
43           Bronx                City Island  40.847247 -73.786488   
44           Bronx                    Fordham  40.860997 -73.896427   
45           Bronx             Morris Heights  40.847898 -73.919672   
46           Bronx         University Heights  40.855727 -73.910416   
47           Bronx               East Tremont  40.842696 -73.887356   
48           Bronx                Port Morris  40.801664 -73.913221   
49        Brooklyn          East Williamsburg  40.708492 -73.938858   
50        Brooklyn               Spring Creek  40.657139 -73.869988   
51        Brooklyn                 Georgetown  40.623845 -73.916075   
52        Brooklyn        Prospect Park South  40.647009 -73.962613   
53        Brooklyn                    Midwood  40.625596 -73.957595   
54        Brooklyn                 North Side  40.714823 -73.958809   
55        Brooklyn               Be

We can see that there is a repeated Chelsea neighborhood that is surely causing the problem above with the fourquare API.

Let's visualize the resulting clusters

In [158]:
# create map
map_clustersNY = folium.Map(location=[latitude, longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(ny_merged['Latitude'], ny_merged['Longitude'], ny_merged['Name'], ny_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersNY)
       
map_clustersNY

Like we can see in the map the most comon clusters are the Cluster 2 and Cluster 5. Lets check each of the clusters and analize.

## Examine Clusters of New York

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

#### Cluster 1

In [159]:
ny_merged.loc[ny_merged['Cluster Labels'] == 0, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
2         Throgs Neck         Deli / Bodega           Coffee Shop   
6            Van Nest           Pizza Place         Deli / Bodega   
8             Belmont    Italian Restaurant           Pizza Place   
13     Edgewater Park    Italian Restaurant           Pizza Place   
57         Ocean Hill         Deli / Bodega         Grocery Store   
61           Sea Gate                   Spa                 Beach   
82            Madison            Bagel Shop          Dessert Shop   
119     East New York         Deli / Bodega           Music Venue   
162      Belle Harbor                 Beach                   Pub   
167        Brookville        Nightlife Spot         Deli / Bodega   
168          Bellaire         Deli / Bodega     Convenience Store   
172            Utopia         Deli / Bodega        History Museum   
174   Astoria Heights                Bakery         Bowling Alley   
177        Blissville         Deli / Bodega                 Hotel   
178           Roxbury  Fast Food Restaurant             Irish Pub   
181      North Corona         Deli / Bodega  Gym / Fitness Center   
185        Whitestone       Bubble Tea Shop          Dance Studio   
194         Briarwood         Deli / Bodega  Fast Food Restaurant   
201  South Ozone Park         Deli / Bodega                  Park   
232     Broad Channel           Pizza Place   Sporting Goods Shop   
234       Bay Terrace           Supermarket    Italian Restaurant   
235        Beechhurst          Optical Shop           Supermarket   
236          Steinway   Rental Car Location    Italian Restaurant   
239       South Beach                 Beach                  Pier   
240     Port Richmond         Deli / Bodega   Rental Car Location   
250            Travis                 Hotel         Deli / Bodega   
251     Manor Heights         Deli / Bodega            Bagel Shop   
254       Egbertville            Bagel Shop    Italian Restaurant   
256   Lighthouse Hill    Italian Restaurant                 Trail   
259          New Dorp    Italian Restaurant           Pizza Place   
261      Howland Hook    Italian Restaurant                  Farm   
263       Bay Terrace           Supermarket    Italian Restaurant   
264    New Dorp Beach    Italian Restaurant         Deli / Bodega   
266     Midland Beach                 Beach         Deli / Bodega   
267      Dongan Hills         Deli / Bodega           Pizza Place   
268          Old Town    Italian Restaurant                Bakery   
270          Arrochar              Bus Stop    Italian Restaurant   
275       Tottenville    Italian Restaurant         Deli / Bodega   
285       Shore Acres    Italian Restaurant              Bus Stop   
286     Richmond Town            Bagel Shop    Italian Restaurant   
289       Great Kills           Pizza Place    Italian Restaurant   
296     Arden Heights           Pizza Place              Pharmacy   

               3rd Most Common Venue       4th Most Common Venue  \
2                         Sports Bar                Liquor Store   
6          Middle Eastern Restaurant          Spanish Restaurant   
8                      Deli / Bodega                      Bakery   
13                               Bar               Deli / Bodega   
57   Southern / Soul Food Restaurant                    Bus Stop   
61                       Bus Station                Home Service   
82                               Spa                 Bus Station   
119                            Plaza        Caribbean Restaurant   
162                              Spa               Deli / Bodega   
167                      Yoga Studio              Farmers Market   
168                    Moving Target                 Bus Station   
172                 Basketball Court                      Bakery   
174                      Bus Station               Shopping Mall   
177                       Donut Shop                 Bus Station   
178                   Basebal

#### Cluster 2

In [160]:
ny_merged.loc[ny_merged['Cluster Labels'] == 1, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
107  Mill Island                  Pool           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
107        Farmers Market   Empanada Restaurant    English Restaurant   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
107  Entertainment Service  Ethiopian Restaurant         Event Service   

    9th Most Common Venue 10th Most Common Venue  
107           Event Space                Exhibit

#### Cluster 3

In [161]:
ny_merged.loc[ny_merged['Cluster Labels'] == 2, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name            1st Most Common Venue  \
0                    Wakefield                         Pharmacy   
3                 Country Club                   Sandwich Place   
4                  Parkchester                      Supermarket   
5           Westchester Square             Fast Food Restaurant   
7                  Morris Park                      Pizza Place   
9               Spuyten Duyvil                             Park   
10             North Riverdale                      Pizza Place   
11                   Soundview               Chinese Restaurant   
12                  Pelham Bay                             Bank   
14                   Olinville             Caribbean Restaurant   
15              Pelham Gardens               Spanish Restaurant   
16                   Concourse                    Grocery Store   
17                   Unionport                   Ice Cream Shop   
18                    Edenwald                      Supermarket   
19                  Mount Hope                    Grocery Store   
20                  Mount Eden                         Pharmacy   
21           Concourse Village             Fast Food Restaurant   
22           Claremont Village                    Grocery Store   
23               Schuylerville               Mexican Restaurant   
24                  Morrisania                   Discount Store   
25                 Castle Hill                      Pizza Place   
26                    Longwood        Latin American Restaurant   
27                  Co-op City                      Bus Station   
28                 Hunts Point                             Food   
29                   Fieldston                            River   
30                   Riverdale                      Bus Station   
31                 Kingsbridge                      Pizza Place   
32                    Woodlawn                      Pizza Place   
33                     Norwood                      Pizza Place   
35                  Baychester                       Donut Shop   
36              Pelham Parkway               Italian Restaurant   
37                 Eastchester             Caribbean Restaurant   
38                Bedford Park                            Diner   
39                     Melrose                      Pizza Place   
40                High  Bridge                      Pizza Place   
41                  Mott Haven               Spanish Restaurant   
42                  West Farms                      Bus Station   
43                 City Island                  Harbor / Marina   
44                     Fordham             Fast Food Restaurant   
45              Morris Heights                         Pharmacy   
46          University Heights                      Pizza Place   
47                East Tremont                      Pizza Place   
48                 Port Morris                      Music Venue   
49           East Williamsburg                              Bar   
50                Spring Creek                   Discount Store   
51                  Georgetown                             Bank   
52         Prospect Park South             Caribbean Restaurant   
53                     Midwood                      Pizza Place   
54                  North Side                      Coffee Shop   
55                Bergen Beach                  Harbor / Marina   
56                   City Line                       Donut Shop   
58   Prospect Lefferts Gardens                           Bakery   
59                 Boerum Hill                      Coffee Shop   
60                    Downtown                     Burger Joint   
62                  South Side                              Bar   
63                   Navy Yard                      Film Studio   
64                       Rugby             Caribbean Restaurant   
65               Fort Hamilton               Chinese Restaurant   
66                Clinton Hill                      Pizza Place   
67    

#### Cluster 4

In [162]:
ny_merged.loc[ny_merged['Cluster Labels'] == 3, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
160  Somerville                  Park           Yoga Studio   
238   Todt Hill                  Park           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
160     Electronics Store    English Restaurant  Entertainment Service   
238     Electronics Store    English Restaurant  Entertainment Service   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
160  Ethiopian Restaurant         Event Service           Event Space   
238  Ethiopian Restaurant         Event Service           Event Space   

    9th Most Common Venue 10th Most Common Venue  
160               Exhibit             Eye Doctor  
238               Exhibit             Eye Doctor

#### Cluster 5

In [163]:
ny_merged.loc[ny_merged['Cluster Labels'] == 4, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name       1st Most Common Venue 2nd Most Common Venue  \
282  Emerson Hill  Construction & Landscaping           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
282        Farmers Market   Empanada Restaurant    English Restaurant   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
282  Entertainment Service  Ethiopian Restaurant         Event Service   

    9th Most Common Venue 10th Most Common Venue  
282           Event Space                Exhibit

#### Cluster 6

In [164]:
ny_merged.loc[ny_merged['Cluster Labels'] == 5, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
1        Clason Point                  Park   American Restaurant   
106   Manhattan Beach              Bus Stop                  Café   
237       Grymes Hill              Bus Stop   American Restaurant   
241  Mariner's Harbor    Italian Restaurant         Deli / Bodega   
248      New Brighton              Bus Stop         Deli / Bodega   
252       Willowbrook              Bus Stop            Bagel Shop   
253      Sandy Ground          Home Service          Intersection   
260          Elm Park              Bus Stop    Italian Restaurant   
271         Arlington              Bus Stop         Grocery Store   
272      Graniteville            Food Truck         Grocery Store   
274         Park Hill              Bus Stop  Gym / Fitness Center   
281     Randall Manor              Bus Stop            Bagel Shop   
292        Bloomfield        Discount Store                  Park   

         3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
1    South American Restaurant              Bus Stop         Boat or Ferry   
106                       Food       Harbor / Marina                 Beach   
237                    Dog Run           Yoga Studio        Farmers Market   
241                   Bus Stop                  Farm   Empanada Restaurant   
248                       Park               Daycare            Playground   
252              Deli / Bodega           Pizza Place                   Spa   
253                     Market              Bus Stop           Yoga Studio   
260        American Restaurant            Toll Plaza        Ice Cream Shop   
271     Furniture / Home Store         Deli / Bodega        Farmers Market   
272             Sandwich Place              Bus Stop                  Farm   
274                Coffee Shop                 Hotel    Athletics & Sports   
281              Deli / Bodega           Pizza Place                  Food   
292          Recreation Center            Theme Park              Bus Stop   

     6th Most Common Venue  7th Most Common Venue  8th Most Common Venue  \
1                     Pool          Grocery Store          Event Service   
106         Ice Cream Shop         Sandwich Place             Playground   
237     English Restaurant  Entertainment Service   Ethiopian Restaurant   
241     English Restaurant  Entertainment Service   Ethiopian Restaurant   
248         Discount Store          Bowling Alley            Flower Shop   
252           Intersection  Entertainment Service   Ethiopian Restaurant   
253    Empanada Restaurant     English Restaurant  Entertainment Service   
260          Deli / Bodega            Pizza Place     Chinese Restaurant   
271  Entertainment Service   Ethiopian Restaurant          Event Service   
272     English Restaurant  Entertainment Service   Ethiopian Restaurant   
274            Yoga Studio     Falafel Restaurant     English Restaurant   
281            Flower Shop     English Restaurant  Entertainment Service   
292            Yoga Studio     English Restaurant  Entertainment Service   

     9th Most Common Venue 10th Most Common Venue  
1     Ethiopian Restaurant                   Farm  
106                Factory     English Restaurant  
237          Event Service            Event Space  
241          Event Service            Event Space  
248         Farmers Market  Entertainment Service  
252          Event Service                   Farm  
253   Ethiopian Restaurant          Event Service  
260            Flea Market    Empanada Restaurant  
271            Event Space                Exhibit  
272          Event Service            Event Space  
274  Entertainment Service   Ethiopian Restaurant  
281   Ethiopian Restaurant          Event Service  
292   Ethiopian Restaurant          Event Service

#### Cluster 7

In [165]:
ny_merged.loc[ny_merged['Cluster Labels'] == 6, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
224      Neponsit                 Beach           Yoga Studio   
233  Breezy Point                 Beach                 Trail   

    3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
224     Electronics Store    English Restaurant  Entertainment Service   
233   Monument / Landmark           Yoga Studio                   Farm   

    6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
224  Ethiopian Restaurant          Event Service           Event Space   
233    English Restaurant  Entertainment Service  Ethiopian Restaurant   

    9th Most Common Venue 10th Most Common Venue  
224               Exhibit             Eye Doctor  
233         Event Service            Event Space

#### Cluster 8

In [166]:
ny_merged.loc[ny_merged['Cluster Labels'] == 7, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
34   Williamsbridge             Nightclub                   Bar   
242      Port Ivory                   Bar           Yoga Studio   
287         Oakwood                   Bar                Lawyer   

    3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
34   Caribbean Restaurant            Soup Place            Yoga Studio   
242     Electronics Store    English Restaurant  Entertainment Service   
287           Yoga Studio                  Farm     English Restaurant   

     6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
34      Falafel Restaurant    English Restaurant  Entertainment Service   
242   Ethiopian Restaurant         Event Service            Event Space   
287  Entertainment Service  Ethiopian Restaurant          Event Service   

    9th Most Common Venue 10th Most Common Venue  
34   Ethiopian Restaurant          Event Service  
242               Exhibit             Eye Doctor  
287           Event Space                Exhibit

Now that we can see the clustering of the complete city of New York, even with 8 cluster we can see that the one that takes dominance is the cluster number 3, we can see that most of them have as common place restaurants be it American or Italian and pizza places just in the first ten we can’t see a clear pattern.

## Results <a name="results"></a>

 With the k-means clustering it was a success in classifying the different boroughs in the neighborhoods thanks to the help of the foursquare API that in most of the cases didn’t have any problem calling it. The clusters in each of the borough normally take a step in which most of the neighborhoods fall into one of them and the others are left like outliner neighborhoods, so if you are looking for a similar neighborhood in the same borough you will likely be in the common cluster and find a similar neighborhood without a problem, for the outliners it will be a tough search.
 Now talking about the New York City clustering we can’t say it was a success this kind of process won’t be as effective with data that is so big and with New York having a lot of stores and restaurants repeated in a lot of neighborhoods it can be hard to look in an analytic and cold way which neighborhoods are alike.

## Discussion <a name="discussion"></a>

 Getting a clean and organized dataset is of vital importance to have a smooth work, so it’s important to remark the great work of the open data of New York. Having the right tools it what makes this work possible. Even if the Foursquare API did the job, it has some problems and it would be best to avoid this kind of situations when doing a work, so it’s better to study which tools you are going to use before working in the code and use another type of venues API if you have access or knowledge of one. 

## Conclusion <a name="conclusion"></a>

We were able to archive the aim of the project in a successful clustering of the boroughs, I wouldn’t recommend this kind of analysis if you are working in clustering neighborhoods. The city of New York have a lot of different features, this study didn’t include thinks like urban areas, atmospheres and lifestyle of the people living in it. So even if the neighborhood similitude is of vital importance it’s to the best interest to analyze all the factors that are included when taking a decision or making a study.